In [221]:
from opensea import OpenseaAPI
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains
from selenium.common.exceptions import NoSuchElementException
from selenium.common.exceptions import StaleElementReferenceException
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support import expected_conditions
from selenium.webdriver.support.ui import Select
from datetime import datetime
from datetime import timedelta
from copy import deepcopy
import numpy as np
import pandas as pd
import pyautogui
import tweepy
import config
import webbrowser
import itertools
import time
import json
import re
#Yanir & Amit NFT project

In [222]:
PATH = "/Users/amittabibi/Documents/chromdriver_selenium/chromedriver"
s=Service(PATH) 

In [3]:
# Function that returns a list with the collections names from that category 
# ###############
def Get_category_collection_names(url):
    driver = webdriver.Chrome(service=s)
    driver.get(url)
    driver.maximize_window()
    collections_button_xpath = """//*[@id="main"]/div/div/div[2]/div/div/div[3]/div/div"""
    collections_button=WebDriverWait(driver, 10).until(EC.presence_of_element_located(
    (By.XPATH, collections_button_xpath)))
    time.sleep(3)
    collections_button.click()
    category_collections_names = []
    
    view_collections_window = driver.find_element(By.CLASS_NAME,"CollectionFilterreact__DivContainer-sc-8w13qm-0")
    driver.execute_script("arguments[0].scrollIntoView(true)", view_collections_window)
    
    count = 0
    flag_stop = 0
    MAX_COLLECT = 20000
    
      
    ######################  loop thats scrolls down the small scrollbox to extarct all the elements needed 
    pyautogui.moveTo(275,740)
    for i in range(65):
        pyautogui.vscroll(-10000)
        time.sleep(2)
    ########################    
    
    ignored_exceptions=(NoSuchElementException,StaleElementReferenceException)    
    collections_scrollbox = WebDriverWait(driver, 10,ignored_exceptions=ignored_exceptions)\
                        .until(expected_conditions.presence_of_all_elements_located((By.CLASS_NAME, "CollectionFilter--item-name")))
    for current_collection in collections_scrollbox:
        current_collection_name = current_collection.text
        category_collections_names.append(current_collection_name)
        time.sleep(2)  
        count+=1
        flag_stop +=1
        if(count>=4):
            count = 0
            pyautogui.moveTo(275,740)
            pyautogui.vscroll(-4)
        if(flag_stop == MAX_COLLECT):
            break
    return category_collections_names

In [4]:
# Function that returns the link to a collection page based on its name
#######
def Get_Collection_Link(collection_name):
    driver = webdriver.Chrome(service=s)
    driver.get("https://opensea.io/assets")
    driver.maximize_window()
    collections_button_xpath = """//*[@id="main"]/div/div/div[2]/div/div/div[3]/div/div"""
    collections_button=WebDriverWait(driver, 10).until(EC.presence_of_element_located(
    (By.XPATH, collections_button_xpath)))
    time.sleep(5)
    collections_button.click()
    
    view_collections_window = WebDriverWait(driver, 10).until(EC.presence_of_element_located(
    (By.CLASS_NAME, 'CollectionFilterreact__DivContainer-sc-8w13qm-0')))
    
    driver.execute_script("arguments[0].scrollIntoView(true)", view_collections_window)
    
    collections_link = None
    search_bar = WebDriverWait(driver, 20).until(EC.element_to_be_clickable
                    ((By.XPATH,"""//*[@id="main"]/div/div/div[2]/div/div/div[3]/div/div/div/div/div/div/div[1]/div/input""")))
    search_bar.send_keys(collection_name)
    time.sleep(5)
    
    
    ignored_exceptions=(NoSuchElementException,StaleElementReferenceException)
    
    search_results = driver.find_elements(By.CLASS_NAME,"CollectionFilter--item-name")
    if(len(search_results)>0):
        result = search_results[0]
        time.sleep(5)
        try:
            if(result.text == collection_name):
                result.click()
                time.sleep(6)
                collection_button = WebDriverWait(driver, 15).until(EC.element_to_be_clickable((By.CLASS_NAME, "SearchPills--pill-content"))) 
                try:
                    collection_button.click()
                except ignored_exceptions:
                    collection_button = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.CLASS_NAME, "SearchPills--pill-content"))) 
                    collection_button.click()
                time.sleep(5)
                collections_link = WebDriverWait(driver, 10).until(EC.presence_of_element_located(
                   (By.XPATH, '/html/body/div[4]/div/div/div/footer/a[1]'))).get_attribute('href')
        except:
            search_results = driver.find_elements(By.CLASS_NAME,"CollectionFilter--item-name")
            result = search_results[0]
            if(result.text == collection_name):
                result.click()
                time.sleep(6)
                collection_button = WebDriverWait(driver, 15).until(EC.element_to_be_clickable((By.CLASS_NAME, "SearchPills--pill-content"))) 
                try:
                    collection_button.click()
                except ignored_exceptions:
                    collection_button = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.CLASS_NAME, "SearchPills--pill-content"))) 
                    collection_button.click()
                time.sleep(5)
                collections_link = WebDriverWait(driver, 10).until(EC.presence_of_element_located(
                   (By.XPATH, '/html/body/div[4]/div/div/div/footer/a[1]'))).get_attribute('href')
    driver.quit()            
    return collections_link

In [5]:
# Function that validate if a collection is created within the last 60 days , since there is no release date data
#################
def validate_collection(url):
    driver = webdriver.Chrome(service=s)
    driver.get(url)
    driver.maximize_window()
    volume_dates = driver.find_elements(By.CLASS_NAME,"recharts-text")
    first_volume_date = volume_dates[0].text
    current_date = datetime.today().strftime('%m/%d')
    date_format = '%m/%d'
    current_date_formatted = datetime.strptime(current_date, date_format)   
    today_minus_30_days = current_date_formatted - timedelta(days=30)
    first_volume_date_formatted = datetime.strptime(first_volume_date, date_format)
    driver.quit()
    print(first_volume_date_formatted)
    print(today_minus_30_days)
    if(first_volume_date_formatted.date() <= today_minus_30_days.date()):
        return True
    else:
        return False

In [6]:
# Function that returns the average daily volume based on the last 30 days volume
################
def Get_collection_daily_vol_avg(url):
    driver = webdriver.Chrome(service=s)
    driver.get(url)
    driver.maximize_window()
    time.sleep(2)
    pyautogui.vscroll(-20)
    try:
        menu = driver.find_elements(By.CLASS_NAME,"Inputreact__StyledContainer-sc-3dr67n-0")
        volume_menu = menu[1]
        volume_menu.click()
        time.sleep(2)
        options_for_menu = driver.find_elements(By.CLASS_NAME,"elements__StyledListItem-sc-197zmwo-0")
        last_30_days = options_for_menu[2]
        last_30_days.click()
        time.sleep(3)
        first_volume_bar = driver.find_elements(By.CLASS_NAME,"PriceHistoryStats--value")
        volume_30_days = first_volume_bar[1].text
        volume_30_days = volume_30_days.replace("Ξ","")
        volume_30_days = volume_30_days.replace(",","")
        volume_30_days = float(volume_30_days)
        avg_daily_vol = volume_30_days/30
    except Exception as e:
        print(e)
        avg_daily_vol = None
    driver.quit()
    return avg_daily_vol

In [7]:
def Get_collections_daily_vol_avg_list(collections_url_list):
    collections_activity_url = [] 
    for collection in collections_url_list:
        collection_activity_url = collection+'?tab=activity'
        collections_activity_url.append(collection_activity_url)   
    collections_avg_daily_list = []
    avg_daily_vol_counter = 0
    for collections_activity_page in collections_activity_url:
        try:
            collection_daily_avg_vol = Get_collection_daily_vol_avg(collections_activity_page)
            collections_avg_daily_list.append(collection_daily_avg_vol)
            time.sleep(2)
            avg_daily_vol_counter+=1
            print(avg_daily_vol_counter)
        except Exception as e:
            print(e)
            print("Error on the",avg_daily_vol_counter+1,"collection")
            break
    return collections_avg_daily_list,avg_daily_vol_counter

In [8]:
# function that gets collections names and returns collections links
def Get_collections_links_list_(collections_names_list):
    collections_links_list = []
    links_counter = 0
    for collection_name in collections_names_list:
        try:
            collection_link = Get_Collection_Link(collection_name)
            collections_links_list.append(collection_link)
            time.sleep(2)
            links_counter+=1
            print(links_counter)
        except Exception as e:
            print(e)
            print("Error on the",links_counter+1,"collection")
            break
    return collections_links_list,links_counter

In [9]:
#Function that returns all the features of specific collection as a list (owners,items,floor price,twitter link)
def Get_collection_features(url):
    driver = webdriver.Chrome(service=s)
    try:
        driver.get(url)
    except TimeoutException:
        driver.quit()
        return False
    driver.maximize_window()
    twitter_link = None
    feature_name = None
    features_list = []
    try:
        collection_features = driver.find_elements(By.CLASS_NAME,"Overflowreact__OverflowContainer-sc-10mm0lu-0")
    except:
        collection_features = driver.find_elements(By.CLASS_NAME,"Overflowreact__OverflowContainer-sc-10mm0lu-0")
    count = 0
    check = 0
    if(len(collection_features)>0):
        for feature_obj in collection_features:
            count+=1
            check=0
            feature = feature_obj.text
            if(feature[-1] == 'K'):
                feature_name_0 = feature.replace(".","")
                feature_name = feature_name_0.replace("K","00")
                check+=1
            if(feature[0] == '<'):
                feature_name = feature.replace("<","")
                check+=1
            if(feature == '---'):
                feature_name = None
                check+=1
            if(check == 0):
                feature_name = feature
            features_list.append(feature_name)
            if(count == 3):
                break
        links = driver.find_elements(By.XPATH,"//a[@href]")
        for link in links:
            if ('twitter' in link.get_attribute("href")) and (link.get_attribute('href')!='https://twitter.com/opensea'):
                twitter_link = link.get_attribute("href")
        features_list.append(twitter_link)    
    else:
        features_list = [None,None,None,None]
    driver.quit()
    return features_list            
            
            
            
            

In [10]:
def features_lists_extraction(All_collections_features_list):
    Collections_Items = []
    Collections_Owners = []
    Collections_Floor_Prices = []
    Collections_Twitter_Links = []
    for collection in All_collections_features_list:
        Collections_Items.append(collection[0])
        Collections_Owners.append(collection[1])
        Collections_Floor_Prices.append(collection[2])
        Collections_Twitter_Links.append(collection[3])
    return Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links

In [11]:
def insert_OS_features_into_dataframe(df,range_start,range_end,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links):
    df.loc[range_start:range_end,'Items'] = Collections_Items
    df.loc[range_start:range_end,'Owners'] = Collections_Owners
    df.loc[range_start:range_end,'Floor_Price'] = Collections_Floor_Prices
    df.loc[range_start:range_end,'Twitter_Links'] = Collections_Twitter_Links
    return df

In [12]:
def tweepy_settings():
    consumer_key = "JwzPwWTIy68ZLTbz3OoiXj0IO"
    consumer_secret = "Ne4c1wsgwsikmbfSl5kNR3J2PPgRXgvOxmSzmcmfiYVma7L7OD"
    bearer_token = "AAAAAAAAAAAAAAAAAAAAAEorYAEAAAAAKt87Dff4tDlvP5R8a9UJSrqraw0%3D9BaS85UBG1e0mXwz3bskPfhqUn3JSKpkf81xfz4ZQT81pdp38M"
    access_token = "719431245-3UREVY7HLU2kc388z8a0ADJUfJB5UDwfcEob754N"
    access_token_secret = "Akl4BLKZUlAmJT96BYqFXcsRRLt8U8hefPUKSGpI70NkF"
    auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
    auth.set_access_token(access_token, access_token_secret)
    api = tweepy.API(auth,wait_on_rate_limit=True)
    return api

In [13]:
def Get_Twitter_Features(Collections_twitter_usernames):
    api = tweepy_settings()
    twitter_user_features_BIGLIST = []
    for user_name in Collections_twitter_usernames:
        try:
            user = api.get_user(screen_name=user_name)
            twitter_user_features = []
            account_name = user.name
            followers_count = user.followers_count
            twitter_user_features.append(followers_count)
            following_count = user.friends_count
            twitter_user_features.append(following_count)
            is_verified = user.verified
            twitter_user_features.append(is_verified)
            date_created = (user.created_at).strftime('%m/%d/%Y')
            twitter_user_features.append(date_created)
            twitter_user_features_BIGLIST.append(twitter_user_features)
        except Exception as e:
            print(e)
            twitter_user_features = []
            account_name = None
            followers_count = None
            twitter_user_features.append(followers_count)                                 
            following_count = None
            twitter_user_features.append(following_count)
            is_verified = None
            twitter_user_features.append(is_verified)
            date_created = None
            twitter_user_features.append(date_created)
            twitter_user_features_BIGLIST.append(twitter_user_features)
            continue
    return twitter_user_features_BIGLIST    

In [14]:
# Collecting all max retweets ,likes,replies ,quotes count from twitter users
def Get_Twitter_user_engagement(twitter_usernames):
    bt = "AAAAAAAAAAAAAAAAAAAAAEorYAEAAAAAKt87Dff4tDlvP5R8a9UJSrqraw0%3D9BaS85UBG1e0mXwz3bskPfhqUn3JSKpkf81xfz4ZQT81pdp38M"
    Client = tweepy.Client(bearer_token=bt,wait_on_rate_limit=True)
    api = tweepy_settings()
    all_users_engagements = []
    
    i = 0
    for user in twitter_usernames:
        print('user',i)
        i+=1
        try:
            tweets_ids = []
            retweets_counts = []
            replies_counts = []
            likes_counts = []
            quotes_counts = []
            user_MAX_engagement = []
            for tweet in tweepy.Cursor(api.user_timeline,screen_name=user,include_rts=False).items(100):
                tweets_ids.append(tweet.id)


            response = Client.get_tweets(ids=tweets_ids,tweet_fields=["public_metrics"])
            for metric in response.data:
                engagement_counts = metric.public_metrics
                retweets_counts.append(engagement_counts['retweet_count'])
                replies_counts.append(engagement_counts['reply_count'])
                likes_counts.append(engagement_counts['like_count'])
                quotes_counts.append(engagement_counts['quote_count'])

            user_MAX_engagement.append(max(retweets_counts))
            user_MAX_engagement.append(max(replies_counts))    
            user_MAX_engagement.append(max(likes_counts))    
            user_MAX_engagement.append(max(quotes_counts))   
            all_users_engagements.append(user_MAX_engagement)    
        except Exception as e:
            print(e)
            user_MAX_engagement = [None,None,None,None]
            all_users_engagements.append(user_MAX_engagement)
            

    return all_users_engagements    

In [138]:
def Get_Opensea_Features(collections_slugs_list):
    collections_opensea_features_list = []
    api= OpenseaAPI(apikey='d9744726233d41968430ffd7760837e3')
    count = 0
    for collection_slug in collections_slugs_list:
        print('collection',count)
        count+=1
        try:
            sum_of_traits = 0
            Opensea_features = []
            collection_info = api.collection(collection_slug=collection_slug)
            collection_creation_date = collection_info['collection']['created_date']
            collection_30_day_volume = collection_info['collection']['stats']['thirty_day_volume']
            collection_safelist_status = collection_info['collection']['safelist_request_status']
            for trait,sub_trait in (collection_info['collection']['traits'].items()):
                sum_of_traits += len(sub_trait)

            current_date = datetime.today().strftime('%Y/%m/%d')
            date_format = '%Y/%m/%d'
            current_date_formatted = datetime.strptime(current_date, date_format)   
            today_minus_30_days = current_date_formatted - timedelta(days=30)

            cutting_string_index = collection_creation_date.rfind('T')
            collection_creation_date_cutted = collection_creation_date[:cutting_string_index]
            collection_date_format = '%Y-%m-%d'
            collection_date_formatted = datetime.strptime(collection_creation_date_cutted, collection_date_format)
            if(collection_date_formatted.date() <= today_minus_30_days.date()):
                Opensea_features.append(collection_creation_date_cutted)
                Opensea_features.append(collection_30_day_volume)
                Opensea_features.append(collection_safelist_status)
                Opensea_features.append(sum_of_traits)
            else:
                Opensea_features = [None,None,None,None]
            collections_opensea_features_list.append(Opensea_features)   
        except Exception as e:
            print(e)
            Opensea_features = [None,None,None,None]
            collections_opensea_features_list.append(Opensea_features)
    return collections_opensea_features_list    

In [18]:
#Function that returns a list with the collections names from that category  ONLY FOR DOMAIN NAMES 
# ###############
# def Get_category_collection_names_DN(url):
#     driver = webdriver.Chrome(service=s)
#     driver.get(url)
#     driver.maximize_window()
#     collections_button_xpath = """//*[@id="main"]/div/div/div[2]/div/div/div[3]/div/div"""
#     collections_button=WebDriverWait(driver, 10).until(EC.presence_of_element_located(
#     (By.XPATH, collections_button_xpath)))
#     time.sleep(3)
#     collections_button.click()
#     category_collections_names = []
    
#     view_collections_window = driver.find_element(By.CLASS_NAME,"CollectionFilterreact__DivContainer-sc-8w13qm-0")
#     driver.execute_script("arguments[0].scrollIntoView(true)", view_collections_window)
    
#     count = 0
#     flag_stop = 0
#     MAX_COLLECT = 588
    
      
# #     ######################  loop thats scrolls down the small scrollbox to extarct all the elements needed 
# #     pyautogui.moveTo(275,740)
# #     for i in range(20):
# #         pyautogui.vscroll(-10000)
# #         time.sleep(5)
# #     ########################    
    
#     ignored_exceptions=(NoSuchElementException,StaleElementReferenceException)    
#     collections_scrollbox = WebDriverWait(driver, 10,ignored_exceptions=ignored_exceptions)\
#                         .until(expected_conditions.presence_of_all_elements_located((By.CLASS_NAME, "CollectionFilter--item-name")))
#     while(len(collections_scrollbox) < 580):
#         pyautogui.moveTo(275,740)
#         pyautogui.vscroll(-10000)
#         time.sleep(5)
#         collections_scrollbox = WebDriverWait(driver, 10,ignored_exceptions=ignored_exceptions)\
#                         .until(expected_conditions.presence_of_all_elements_located((By.CLASS_NAME, "CollectionFilter--item-name")))
        
#     print(len(collections_scrollbox))
#     for current_collection in collections_scrollbox:
#         current_collection_name = current_collection.text
#         category_collections_names.append(current_collection_name)
#         time.sleep(5)  
#         count+=1
#         flag_stop +=1
#         if(count>=4):
#             count = 0
#             pyautogui.moveTo(275,740)
#             pyautogui.vscroll(-4)
#         if(flag_stop == MAX_COLLECT):
#             break
#     return category_collections_names


# domain_names_url ='https://opensea.io/assets?search[categories][0]=domain-names'
# domain_names_collections_names = Get_category_collection_names(domain_names_url)
# print(len(domain_names_collections_names))


# with open("DomainNames_Category_Collections_Names.json", "w") as outfile:
#     json.dump(domain_names_collections_names, outfile)

In [ ]:
#Function that returns a list with the collections names from that category ONLY FOR VIRTUAL WORLDS
###############
# def Get_category_collection_names_VW(url):
#     driver = webdriver.Chrome(service=s)
#     driver.get(url)
#     driver.maximize_window()
#     collections_button_xpath = """//*[@id="main"]/div/div/div[2]/div/div/div[3]/div/div"""
#     collections_button=WebDriverWait(driver, 10).until(EC.presence_of_element_located(
#     (By.XPATH, collections_button_xpath)))
#     time.sleep(3)
#     collections_button.click()
#     category_collections_names = []
    
#     view_collections_window = driver.find_element(By.CLASS_NAME,"CollectionFilterreact__DivContainer-sc-8w13qm-0")
#     driver.execute_script("arguments[0].scrollIntoView(true)", view_collections_window)
    
#     count = 0
#     flag_stop = 0
#     MAX_COLLECT = 2437
    
      
# #     ######################  loop thats scrolls down the small scrollbox to extarct all the elements needed 
# #     pyautogui.moveTo(275,740)
# #     for i in range(50):
# #         pyautogui.vscroll(-10000)
# #         time.sleep(3)
# #     ########################    

#     ignored_exceptions=(NoSuchElementException,StaleElementReferenceException)    
#     collections_scrollbox = WebDriverWait(driver, 10,ignored_exceptions=ignored_exceptions)\
#                         .until(expected_conditions.presence_of_all_elements_located((By.CLASS_NAME, "CollectionFilter--item-name")))
#     while(len(collections_scrollbox) < 2430):
#         pyautogui.moveTo(275,740)
#         pyautogui.vscroll(-1000)
#         time.sleep(3)
#         collections_scrollbox = WebDriverWait(driver, 10,ignored_exceptions=ignored_exceptions)\
#                         .until(expected_conditions.presence_of_all_elements_located((By.CLASS_NAME, "CollectionFilter--item-name")))
#     print(len(collections_scrollbox))
#     for current_collection in collections_scrollbox:
#         current_collection_name = current_collection.text
#         category_collections_names.append(current_collection_name)
#         time.sleep(2)  
#         count+=1
#         flag_stop +=1
#         if(count>=4):
#             count = 0
#             pyautogui.moveTo(275,740)
#             pyautogui.vscroll(-4)
#         if(flag_stop == MAX_COLLECT):
#             break
#     return category_collections_names

# virtual_worlds_url = "https://opensea.io/assets?search[categories][0]=virtual-worlds"
# virtual_worlds_url_collections_names_list = Get_category_collection_names(virtual_worlds_url)


# with open('VirtualWorlds_Category_Collections_Names.json','w') as outfile:
#     json.dump(virtual_worlds_url_collections_names_list, outfile)

In [ ]:
#Extracting TRADING CARDS 
url ='https://opensea.io/assets?search[categories][0]=trading-cards'
trading_cards_names_list=Get_category_collection_names(url)

with open('Trading_Cards_Category_Collections_Names.txt','w') as f:
    json.dump(trading_cards_names_list,f)

In [ ]:
url ='https://opensea.io/assets?search[categories][0]=photography-category'
photography_names_list2=Get_category_collection_names(url)

with open('Photography_Category_Collections_Names.json','w') as jsonFile:
    json.dump(photography_names_list2, jsonFile)

In [ ]:
##Extracting UTILITY
utility_url = "https://opensea.io/assets?search[categories][0]=utility"
utility_collections_names = Get_category_collection_names(utility_url)

with open('Utility_Category_Collectons_Names.json','w')as f:
    json.dump(utility_collections_names,f)

In [ ]:
##Extracting SPORTS
sports_url = "https://opensea.io/assets?search[categories][0]=sports"
sports_category_collections_names = Get_category_collection_names(sports_url)

with open('Sports_Category_Collections_Names.json', 'w') as f:
    json.dump(sports_category_collections_names, f)

In [ ]:
##Rest of the collections were extracted via other computers  and not saved but
##its the same code for the rest of them

In [9]:
f = open('Art_Category_Collections_Names.json')
Art_Category_Collections_Names = json.load(f)
dictOf_Art_Names = { i : 'Art' for i in Art_Category_Collections_Names }

f = open('Collectibles_Category_Collections_Names.json')
Collectibles_Category_Collections_Names = json.load(f)
dictOf_Collectibles_Names = { i : 'Collectibles' for i in Collectibles_Category_Collections_Names }

f = open('DomainNames_Category_Collections_Names.json')
DomainNames_Category_Collections_Names = json.load(f)
dictOf_DomainNames_Names = { i : 'Domain Names' for i in DomainNames_Category_Collections_Names }

f = open('music_names_list.json')
Music_Category_Collections_Names = json.load(f)
dictOf_Music_Names = { i : 'Music' for i in Music_Category_Collections_Names }

f = open('Photography_Category_Collections_Names.json')
Photography_Category_Collections_Names = json.load(f)
dictOf_Photography_Names = { i : 'Photography' for i in Photography_Category_Collections_Names }

f = open('Sports_Category_Collections_Names.json')
Sports_Category_Collections_Names = json.load(f)
dictOf_Sports_Names = { i : 'Sports' for i in Sports_Category_Collections_Names }

f = open('Trading_Cards_Category_Collections_Names.json')
Trading_Cards_Category_Collections_Names = json.load(f)
dictOf_TradingCards_Names = { i : 'Trading Cards' for i in Trading_Cards_Category_Collections_Names }

f = open('Utility_Category_Collectons_Names.json')
Utility_Category_Collectons_Names = json.load(f)
dictOf_Utility_Names = { i : 'Utility' for i in Utility_Category_Collectons_Names }

f = open('VirtualWorlds_Category_Collections_Names.json')
VirtualWorlds_Category_Collections_Names = json.load(f)
dictOf_VirtualWorlds_Names = { i : 'Virtual Worlds' for i in VirtualWorlds_Category_Collections_Names }

In [10]:
dict_list_collections_names = [dictOf_Art_Names,dictOf_Collectibles_Names,dictOf_DomainNames_Names,
                              dictOf_Music_Names,dictOf_Photography_Names,dictOf_Sports_Names,
                              dictOf_TradingCards_Names,dictOf_Utility_Names,dictOf_VirtualWorlds_Names]

In [11]:
df = pd.DataFrame([(i, j) for a in dict_list_collections_names for i, j in a.items()], 
                   columns=['Collection_Name','Category'])

In [12]:
df_after_dummies = pd.get_dummies(df,columns=['Category'])

In [13]:
df_after_dummies

Collection_Name  Category_Art  Category_Collectibles  \
0      Bored Ape Yacht Club             1                      0   
1               CryptoPunks             1                      0   
2        Art Blocks Curated             1                      0   
3               Janky Heist             1                      0   
4                PhantaBear             1                      0   
...                     ...           ...                    ...   
36958           GreyPanther             0                      0   
36959    birds - zvarnoCurk             0                      0   
36960  flowers - U2Q5Rj1cUF             0                      0   
36961              Bento V4             0                      0   
36962  MONOCHROMEandMINIMAL             0                      0   

       Category_Domain Names  Category_Music  Category_Photography  \
0                          0               0                     0   
1                          0               0                     0   
2                          0               0                     0   
3                          0               0                     0   
4                          0               0                     0   
...                      ...             ...                   ...   
36958                      0               0                     0   
36959                      0               0                     0   
36960                      0               0                     0   
36961                      0               0                     0   
36962                      0               0                     0   

       Category_Sports  Category_Trading Cards  Category_Utility  \
0                    0                       0                 0   
1                    0                       0                 0   
2                    0                       0                 0   
3                    0                       0                 0   
4                    0                       0                 0   
...                ...                     ...               ...   
36958                0                       0                 0   
36959                0                       0                 0   
36960                0                       0                 0   
36961                0                       0                 0   
36962                0                       0                 0   

       Category_Virtual Worlds  
0                            0  
1                            0  
2                            0  
3                            0  
4                            0  
...                        ...  
36958                        1  
36959                        1  
36960                        1  
36961                        1  
36962                        1  

[36963 rows x 10 columns]

In [14]:
df_no_duplicates = df_after_dummies.groupby('Collection_Name',as_index=False).sum()

In [15]:
df_no_duplicates

Collection_Name  Category_Art  \
0                                  ! poP twtzZ. c^!_0 *]             0   
1                                          !!Cancelled!!             0   
2                                 " Code of The Nature "             0   
3                                        " THE PRELUDE "             1   
4      "20 FTNC" collection items protected by copyri...             0   
...                                                  ...           ...   
36027                                  ~ Light My Fire ~             0   
36028                                   ~Asylum Inmates~             0   
36029                                       ~Free world~             0   
36030                                          ~~Waves~~             0   
36031                      ♫ ByteBeats by DADABOTS x KAI             1   

       Category_Collectibles  Category_Domain Names  Category_Music  \
0                          0                      0               0   
1                          1                      0               0   
2                          0                      0               1   
3                          0                      0               0   
4                          0                      0               0   
...                      ...                    ...             ...   
36027                      0                      0               0   
36028                      0                      0               0   
36029                      0                      0               0   
36030                      1                      0               0   
36031                      0                      0               0   

       Category_Photography  Category_Sports  Category_Trading Cards  \
0                         0                0                       1   
1                         0                0                       0   
2                         0                0                       0   
3                         0                0                       0   
4                         0                1                       0   
...                     ...              ...                     ...   
36027                     1                0                       0   
36028                     0                0                       1   
36029                     1                0                       0   
36030                     0                0                       0   
36031                     0                0                       0   

       Category_Utility  Category_Virtual Worlds  
0                     0                        0  
1                     0                        0  
2                     0                        0  
3                     0                        0  
4                     0                        0  
...                 ...                      ...  
36027                 0                        0  
36028                 0                        1  
36029                 0                        0  
36030                 0                        0  
36031                 0                        0  

[36032 rows x 10 columns]

In [16]:
df_no_duplicates.to_csv('Dataframe_excluding_features_and_volume.csv')

In [17]:
Collections_Names_List = df_no_duplicates['Collection_Name'].tolist()

In [18]:
with open('Collections_Names_List.json', 'w') as f:
    json.dump(Collections_Names_List, f)

In [19]:
Collections_Names_List

['! poP twtzZ. c^!_0 *]',
 '!!Cancelled!!',
 '" Code of The Nature "',
 '" THE PRELUDE "',
 '"20 FTNC" collection items protected by copyright. V3',
 '"20 FTNC" in this collection.',
 '"26 FTNC" in this collection',
 '"37 FTNC" in this collection',
 '"50 VBNC group E" in this collection, items protected by copyright',
 '"A world of colors" by Cinthia Ponce V3',
 '"ALCHEMIST" by Blue the Great',
 '"APE YACHT CLUB" HALLOWEEN SPECIAL EDITION',
 '"ASTRO CUBEZ" V.1',
 '"Amnesia" by Pat Dimitri',
 '"Artists Mood" by Oscar Latuag',
 '"Away I Flew - Visual Poetry of Being Human". Photography by Jerad Armijo - 61 1/1 NFTs',
 '"BLOODY"',
 '"Ballers" Epic Moments in Sports 8bit',
 '"Bird\'s eye view" Drone Aerial Photography',
 '"Bloat" JaaDaan',
 '"Boji", the wandering dog of Istanbul.',
 '"CRYPTO PICASSO"',
 '"CRYPTOGNOSIS" TAROT',
 '"Charged Up Culture"',
 '"Cities" (Second Album)',
 '"Creepto Surrealism" by Eye Sticker',
 '"Cuba" A place that stole my heart',
 '"Download My Heart" Collection'

In [20]:
df_no_duplicates["Collections_Links"] = None

In [21]:
df_20k_rows = df_no_duplicates.drop(df_no_duplicates.index[20875:], axis=0,inplace=False)

In [22]:
df_20k_rows_copy = df_20k_rows.drop(df_no_duplicates.index[:875], axis=0)

In [23]:
df_20k_Collections = df_20k_rows_copy.reset_index()

In [24]:
df_20k_Collections

index                              Collection_Name  Category_Art  \
0        875                                        A & C             0   
1        876  A 2D representation of a Brushless DC Motor             0   
2        877                            A Bathing Kitsune             0   
3        878                           A Beautiful Nature             0   
4        879                 A Beautiful moments in Japan             0   
...      ...                                          ...           ...   
19995  20870                                     Over Sky             0   
19996  20871            Over the Fog it feels like Heaven             0   
19997  20872                             Overcast Glacier             0   
19998  20873                     Overheard on Wall Street             0   
19999  20874                                     Overside             0   

       Category_Collectibles  Category_Domain Names  Category_Music  \
0                          0                      0               0   
1                          0                      0               0   
2                          0                      0               0   
3                          0                      0               0   
4                          0                      0               0   
...                      ...                    ...             ...   
19995                      0                      0               0   
19996                      0                      0               0   
19997                      0                      0               0   
19998                      1                      0               0   
19999                      0                      0               0   

       Category_Photography  Category_Sports  Category_Trading Cards  \
0                         0                0                       0   
1                         0                0                       0   
2                         0                0                       1   
3                         1                0                       0   
4                         1                0                       0   
...                     ...              ...                     ...   
19995                     0                0                       0   
19996                     1                0                       0   
19997                     1                0                       0   
19998                     0                0                       0   
19999                     0                0                       0   

       Category_Utility  Category_Virtual Worlds Collections_Links  
0                     1                        0              None  
1                     1                        0              None  
2                     0                        0              None  
3                     0                        0              None  
4                     0                        0              None  
...                 ...                      ...               ...  
19995                 1                        0              None  
19996                 0                        0              None  
19997                 0                        0              None  
19998                 0                        0              None  
19999                 1                        0              None  

[20000 rows x 12 columns]

In [25]:
df_20k_Collections.drop('index',axis=1,inplace=True)

In [26]:
df_20k_Collections

Collection_Name  Category_Art  \
0                                            A & C             0   
1      A 2D representation of a Brushless DC Motor             0   
2                                A Bathing Kitsune             0   
3                               A Beautiful Nature             0   
4                     A Beautiful moments in Japan             0   
...                                            ...           ...   
19995                                     Over Sky             0   
19996            Over the Fog it feels like Heaven             0   
19997                             Overcast Glacier             0   
19998                     Overheard on Wall Street             0   
19999                                     Overside             0   

       Category_Collectibles  Category_Domain Names  Category_Music  \
0                          0                      0               0   
1                          0                      0               0   
2                          0                      0               0   
3                          0                      0               0   
4                          0                      0               0   
...                      ...                    ...             ...   
19995                      0                      0               0   
19996                      0                      0               0   
19997                      0                      0               0   
19998                      1                      0               0   
19999                      0                      0               0   

       Category_Photography  Category_Sports  Category_Trading Cards  \
0                         0                0                       0   
1                         0                0                       0   
2                         0                0                       1   
3                         1                0                       0   
4                         1                0                       0   
...                     ...              ...                     ...   
19995                     0                0                       0   
19996                     1                0                       0   
19997                     1                0                       0   
19998                     0                0                       0   
19999                     0                0                       0   

       Category_Utility  Category_Virtual Worlds Collections_Links  
0                     1                        0              None  
1                     1                        0              None  
2                     0                        0              None  
3                     0                        0              None  
4                     0                        0              None  
...                 ...                      ...               ...  
19995                 1                        0              None  
19996                 0                        0              None  
19997                 0                        0              None  
19998                 0                        0              None  
19999                 1                        0              None  

[20000 rows x 11 columns]

In [27]:
f = open('From_0_Until_387_All_Collections_Links.json')
From_0_Until_387_All_Collections_Links = json.load(f)
len(From_0_Until_387_All_Collections_Links)

387

In [37]:
## Adding the collections links to the dataframe for validating purposes
df_20k_Collections.loc[0:386,'Collections_Links'] = From_0_Until_387_All_Collections_Links 

In [38]:
f = open('From_2000Until_2416_All_Collections_Links.json')
From_2000Until_2416_All_Collections_Links = json.load(f)
len(From_2000Until_2416_All_Collections_Links)

416

In [39]:
df_20k_Collections.loc[2000:2415,'Collections_Links'] = From_2000Until_2416_All_Collections_Links

In [40]:
f = open('From_2417_Until_2797_All_Collections_Links.json')
From_2417_Until_2797_All_Collections_Links = json.load(f)
len(From_2417_Until_2797_All_Collections_Links)

380

In [41]:
df_20k_Collections.loc[2417:2796,'Collections_Links'] = From_2417_Until_2797_All_Collections_Links

In [42]:
f = open('From_4000_Until_808_All_Collections_Links.json')
From_4000_Until_808_All_Collections_Links = json.load(f)

In [43]:
df_20k_Collections.loc[4000:4807,'Collections_Links'] = From_4000_Until_808_All_Collections_Links

In [195]:
f = open('From_4809_Until_5178_All_Collections_Links.json')
From_4809_Until_5178_All_Collections_Links = json.load(f)
df_20k_Collections.loc[4809:5177,'Collections_Links'] = From_4809_Until_5178_All_Collections_Links

In [45]:
df_20k_Collections.to_csv('df_20k_Collections_progress_1.csv') #### continue adding to the dataframe in the next session

In [191]:
df_20k_progress1 = pd.read_csv('df_20k_Collections_progress_1.csv')

In [196]:
f = open('From_388_Until_569_All_Collections_Links.json')
From_388_Until_569_All_Collections_Links = json.load(f)
df_20k_Collections.loc[388:568,'Collections_Links'] = From_388_Until_569_All_Collections_Links

In [198]:
f = open('From_570_Until_627_All_Collections_Links.json')
From_570_Until_627_All_Collections_Links = json.load(f)
df_20k_Collections.loc[570:626,'Collections_Links'] = From_570_Until_627_All_Collections_Links

In [201]:
f = open('From_628_Until_714_All_Collections_Links.json')
From_628_Until_714_All_Collections_Links = json.load(f)
df_20k_Collections.loc[628:713,'Collections_Links'] = From_628_Until_714_All_Collections_Links

In [203]:
f = open('From_715_Until_858_All_Collections_Links.json')
From_715_Until_858_All_Collections_Links = json.load(f)
df_20k_Collections.loc[715:857,'Collections_Links'] = From_715_Until_858_All_Collections_Links

In [205]:
f = open('From_859_Until_915_All_Collections_Links.json')
From_859_Until_915_All_Collections_Links = json.load(f)
df_20k_Collections.loc[859:914,'Collections_Links'] = From_859_Until_915_All_Collections_Links

In [207]:
f = open('From_916_Until_998_All_Collections_Links.json')
From_916_Until_998_All_Collections_Links = json.load(f)
df_20k_Collections.loc[916:997,'Collections_Links'] = From_916_Until_998_All_Collections_Links

In [209]:
f = open('From_999_Until_1329_All_Collections_Links.json')
From_999_Until_1329_All_Collections_Links = json.load(f)
df_20k_Collections.loc[999:1328,'Collections_Links'] = From_999_Until_1329_All_Collections_Links

In [216]:
f = open('From_1330_Until_1382_All_Collections_Links.json')
From_1330_Until_1382_All_Collections_Links = json.load(f)
df_20k_Collections.loc[1330:1381,'Collections_Links'] = From_1330_Until_1382_All_Collections_Links

In [222]:
f = open('From_1383_Until_1483_All_Collections_Links.json')
From_1383_Until_1483_All_Collections_Links = json.load(f)
df_20k_Collections.loc[1383:1482,'Collections_Links'] = From_1383_Until_1483_All_Collections_Links

In [225]:
f = open('From_1484_Until_1747_All_Collections_Links.json')
From_1484_Until_1747_All_Collections_Links = json.load(f)
df_20k_Collections.loc[1484:1746,'Collections_Links'] = From_1484_Until_1747_All_Collections_Links

In [227]:
f = open('From_1748_Until_1908_All_Collections_Links.json')
From_1748_Until_1908_All_Collections_Links = json.load(f)
df_20k_Collections.loc[1748:1907,'Collections_Links'] = From_1748_Until_1908_All_Collections_Links

In [229]:
f = open('From_1909_Until_1999_All_Collections_Links.json')
From_1909_Until_1999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[1909:1998,'Collections_Links'] = From_1909_Until_1999_All_Collections_Links

In [231]:
f = open('From_2798_Until_2835_All_Collections_Links.json')
From_2798_Until_2835_All_Collections_Links = json.load(f)
df_20k_Collections.loc[2798:2834,'Collections_Links'] = From_2798_Until_2835_All_Collections_Links

In [234]:
f = open('From_2836_Until_3268_All_Collections_Links.json')
From_2836_Until_3268_All_Collections_Links = json.load(f)
df_20k_Collections.loc[2836:3267,'Collections_Links'] = From_2836_Until_3268_All_Collections_Links

In [236]:
f = open('From_3269_Until_3371_All_Collections_Links.json')
From_3269_Until_3371_All_Collections_Links = json.load(f)
df_20k_Collections.loc[3269:3370,'Collections_Links'] = From_3269_Until_3371_All_Collections_Links

In [238]:
f = open('From_3372_Until_3439_All_Collections_Links.json')
From_3372_Until_3439_All_Collections_Links = json.load(f)
df_20k_Collections.loc[3372:3438,'Collections_Links'] = From_3372_Until_3439_All_Collections_Links

In [242]:
f = open('From_3440_Until_3739_All_Collections_Links.json')
From_3440_Until_3739_All_Collections_Links = json.load(f)
df_20k_Collections.loc[3440:3738,'Collections_Links'] = From_3440_Until_3739_All_Collections_Links

In [244]:
f = open('From_3740_Until_3858_All_Collections_Links.json')
From_3740_Until_3858_All_Collections_Links = json.load(f)
df_20k_Collections.loc[3740:3857,'Collections_Links'] = From_3740_Until_3858_All_Collections_Links

In [246]:
f = open('From_3859_Until_3999_All_Collections_Links.json')
From_3859_Until_3999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[3859:3998,'Collections_Links'] = From_3859_Until_3999_All_Collections_Links

In [248]:
f = open('From_5179_Until_5226_All_Collections_Links.json')
From_5179_Until_5226_All_Collections_Links = json.load(f)
df_20k_Collections.loc[5179:5225,'Collections_Links'] = From_5179_Until_5226_All_Collections_Links

In [250]:
f = open('From_5227_Until_5332_All_Collections_Links.json')
From_5227_Until_5332_All_Collections_Links = json.load(f)
df_20k_Collections.loc[5227:5331,'Collections_Links'] = From_5227_Until_5332_All_Collections_Links

In [253]:
f = open('From_5333_Until_5649_All_Collections_Links.json')
From_5333_Until_5649_All_Collections_Links = json.load(f)
df_20k_Collections.loc[5333:5648,'Collections_Links'] = From_5333_Until_5649_All_Collections_Links

In [256]:
f = open('From_5650_Until_5925_All_Collections_Links.json')
From_5650_Until_5925_All_Collections_Links = json.load(f)
df_20k_Collections.loc[5650:5924,'Collections_Links'] = From_5650_Until_5925_All_Collections_Links

In [258]:
f = open('From_5923_Until_5974_All_Collections_Links.json')
From_5923_Until_5974_All_Collections_Links = json.load(f)
df_20k_Collections.loc[5923:5973,'Collections_Links'] = From_5923_Until_5974_All_Collections_Links

In [260]:
f = open('From_5975_Until_5999_All_Collections_Links.json')
From_5975_Until_5999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[5975:5998,'Collections_Links'] = From_5975_Until_5999_All_Collections_Links

In [262]:
f = open('from_6000Until_6318_All_Collections_Links.json')
from_6000Until_6318_All_Collections_Links = json.load(f)
df_20k_Collections.loc[6000:6317,'Collections_Links'] = from_6000Until_6318_All_Collections_Links

In [264]:
f = open('From_6319_Until_6371_All_Collections_Links.json')
From_6319_Until_6371_All_Collections_Links = json.load(f)
df_20k_Collections.loc[6319:6370,'Collections_Links'] = From_6319_Until_6371_All_Collections_Links

In [266]:
f = open('From_6372_Until_6653_All_Collections_Links.json')
From_6372_Until_6653_All_Collections_Links = json.load(f)
df_20k_Collections.loc[6372:6652,'Collections_Links'] = From_6372_Until_6653_All_Collections_Links

In [268]:
f = open('From_6654_Until_6789_All_Collections_Links.json')
From_6654_Until_6789_All_Collections_Links = json.load(f)
df_20k_Collections.loc[6654:6788,'Collections_Links'] = From_6654_Until_6789_All_Collections_Links

In [270]:
f = open('From_6790_Until_6835_All_Collections_Links.json')
From_6790_Until_6835_All_Collections_Links = json.load(f)
df_20k_Collections.loc[6790:6834,'Collections_Links'] = From_6790_Until_6835_All_Collections_Links

In [272]:
f = open('From_6836_Until_7260_All_Collections_Links.json')
From_6836_Until_7260_All_Collections_Links = json.load(f)
df_20k_Collections.loc[6836:7259,'Collections_Links'] = From_6836_Until_7260_All_Collections_Links

In [274]:
f = open('From_7261_Until_7443_All_Collections_Links.json')
From_7261_Until_7443_All_Collections_Links = json.load(f)
df_20k_Collections.loc[7261:7442,'Collections_Links'] = From_7261_Until_7443_All_Collections_Links

In [276]:
f = open('From_7444_Until_7731_All_Collections_Links.json')
From_7444_Until_7731_All_Collections_Links = json.load(f)
df_20k_Collections.loc[7444:7730,'Collections_Links'] = From_7444_Until_7731_All_Collections_Links

In [278]:
f = open('From_7732_Until_7778_All_Collections_Links.json')
From_7732_Until_7778_All_Collections_Links = json.load(f)
df_20k_Collections.loc[7732:7777,'Collections_Links'] = From_7732_Until_7778_All_Collections_Links

In [280]:
f = open('From_7779_Until_7847_All_Collections_Links.json')
From_7779_Until_7847_All_Collections_Links = json.load(f)
df_20k_Collections.loc[7779:7846,'Collections_Links'] = From_7779_Until_7847_All_Collections_Links

In [285]:
f = open('From_7847_Until_7999_All_Collections_Links.json')
From_7847_Until_7999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[7847:7998,'Collections_Links'] = From_7847_Until_7999_All_Collections_Links

In [288]:
f = open('From_8000_Until_8339_All_Collections_Links.json')
From_8000_Until_8339_All_Collections_Links = json.load(f)
df_20k_Collections.loc[8000:8338,'Collections_Links'] = From_8000_Until_8339_All_Collections_Links

In [291]:
f = open('From_8340_Until_8481_All_Collections_Links.json')
From_8340_Until_8481_All_Collections_Links = json.load(f)
df_20k_Collections.loc[8340:8480,'Collections_Links'] = From_8340_Until_8481_All_Collections_Links

In [294]:
f = open('From_8482_Until_8696_All_Collections_Links.json')
From_8482_Until_8696_All_Collections_Links = json.load(f)
df_20k_Collections.loc[8482:8695,'Collections_Links'] = From_8482_Until_8696_All_Collections_Links

In [297]:
f = open('From_8697_Until_8810_All_Collections_Links.json')
From_8697_Until_8810_All_Collections_Links = json.load(f)
df_20k_Collections.loc[8697:8809,'Collections_Links'] = From_8697_Until_8810_All_Collections_Links

In [298]:
f = open('From_8811_Until_8860_All_Collections_Links.json')
From_8811_Until_8860_All_Collections_Links = json.load(f)
df_20k_Collections.loc[8811:8859,'Collections_Links'] = From_8811_Until_8860_All_Collections_Links

In [300]:
f = open('From_8861_Until_9032_All_Collections_Links.json')
From_8861_Until_9032_All_Collections_Links = json.load(f)
df_20k_Collections.loc[8861:9031,'Collections_Links'] = From_8861_Until_9032_All_Collections_Links

In [304]:
f = open('From_9033_Until_9281_All_Collections_Links.json')
From_9033_Until_9281_All_Collections_Links = json.load(f)
df_20k_Collections.loc[9033:9280,'Collections_Links'] = From_9033_Until_9281_All_Collections_Links

In [307]:
f = open('From_9282_Until_9605_All_Collections_Links.json')
From_9282_Until_9605_All_Collections_Links = json.load(f)
df_20k_Collections.loc[9282:9604,'Collections_Links'] = From_9282_Until_9605_All_Collections_Links

In [308]:
df_20k_Collections.to_csv('df_20k_Collections_progress_2.csv') #### continue adding to the dataframe in the next session

In [341]:
df_20k_Collections.loc[16000:16113]

Collection_Name  Category_Art  Category_Collectibles  \
16000                  Magic Flasks             1                      0   
16001           Magic Football NFTs             0                      0   
16002        Magic Internet Potions             0                      0   
16003               Magic Money NFT             0                      0   
16004            Magic Movie Moment             0                      0   
...                             ...           ...                    ...   
16109          Manchester City Logo             0                      0   
16110  Manchester City Player Cards             0                      0   
16111            Manchester Heights             0                      0   
16112          Manchester United #1             0                      0   
16113     Manchester United 2021/22             0                      0   

       Category_Domain Names  Category_Music  Category_Photography  \
16000                      0               0                     0   
16001                      0               0                     0   
16002                      0               0                     0   
16003                      0               0                     0   
16004                      0               0                     1   
...                      ...             ...                   ...   
16109                      0               0                     0   
16110                      0               0                     0   
16111                      0               0                     0   
16112                      0               0                     0   
16113                      0               0                     0   

       Category_Sports  Category_Trading Cards  Category_Utility  \
16000                0                       0                 0   
16001                1                       0                 0   
16002                0                       0                 0   
16003                0                       0                 1   
16004                0                       0                 0   
...                ...                     ...               ...   
16109                1                       0                 0   
16110                1                       0                 0   
16111                0                       1                 0   
16112                1                       0                 0   
16113                1                       0                 0   

       Category_Virtual Worlds Collections_Links  
16000                        0              None  
16001                        0              None  
16002                        1              None  
16003                        0              None  
16004                        0              None  
...                        ...               ...  
16109                        0              None  
16110                        0              None  
16111                        0              None  
16112                        0              None  
16113                        0              None  

[114 rows x 11 columns]

In [312]:
###Extracting collections links by their names
##########################################
f = open("Collections_Names_List_20k.json")
names_list = json.load(f)
range_start = 9860
range_end = 9999
name_list_small = names_list[range_start:range_end]

last_link_index = 0 #intialize
first_link_index = str(range_start)
Collections_links,last_link_index = Get_collections_links_list_(name_list_small)
print(len(Collections_links))

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
139


In [313]:
last_link_index += range_start
end_index = str(last_link_index)

In [314]:
with open("From_"+first_link_index+"_Until_"+end_index+"_All_Collections_Links.json", "w") as f:
    json.dump(Collections_links, f)    

In [355]:
f = open('From_9606_Until_9752_All_Collections_Links.json')
From_9606_Until_9752_All_Collections_Links = json.load(f)
df_20k_Collections.loc[9606:9751,'Collections_Links'] = From_9606_Until_9752_All_Collections_Links

In [358]:
f = open('From_9753_Until_9859_All_Collections_Links.json')
From_9753_Until_9859_All_Collections_Links = json.load(f)
df_20k_Collections.loc[9753:9858,'Collections_Links'] = From_9753_Until_9859_All_Collections_Links

In [360]:
f = open('From_9860_Until_9999_All_Collections_Links.json')
From_9860_Until_9999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[9860:9998,'Collections_Links'] = From_9860_Until_9999_All_Collections_Links

In [363]:
f = open('From_10000_Until_11122_All_Collections_Links.json')
From_10000_Until_11122_All_Collections_Links = json.load(f)
df_20k_Collections.loc[10000:11121,'Collections_Links'] = From_10000_Until_11122_All_Collections_Links

In [365]:
f = open('From_11123_Until_11187_All_Collections_Links.json')
From_11123_Until_11187_All_Collections_Links = json.load(f)
df_20k_Collections.loc[11123:11186,'Collections_Links'] = From_11123_Until_11187_All_Collections_Links

In [367]:
f = open('From_11187_Until_11372_All_Collections_Links.json')
From_11187_Until_11372_All_Collections_Links = json.load(f)
df_20k_Collections.loc[11187:11371,'Collections_Links'] = From_11187_Until_11372_All_Collections_Links

In [369]:
f = open('From_11373_Until_11593_All_Collections_Links.json')
From_11373_Until_11593_All_Collections_Links = json.load(f)
df_20k_Collections.loc[11373:11592,'Collections_Links'] = From_11373_Until_11593_All_Collections_Links

In [371]:
f = open('From_11594_Until_11883_All_Collections_Links.json')
From_11594_Until_11883_All_Collections_Links = json.load(f)
df_20k_Collections.loc[11594:11882,'Collections_Links'] = From_11594_Until_11883_All_Collections_Links

In [373]:
f = open('From_11884_Until_11999_All_Collections_Links.json')
From_11884_Until_11999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[11884:11998,'Collections_Links'] = From_11884_Until_11999_All_Collections_Links

In [375]:
f = open('From_12000_Until_12420_All_Collections_Links.json')
From_12000_Until_12420_All_Collections_Links = json.load(f)
df_20k_Collections.loc[12000:12419,'Collections_Links'] = From_12000_Until_12420_All_Collections_Links

In [377]:
f = open('From_12421_Until_12999_All_Collections_Links.json')
From_12421_Until_12999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[12421:12998,'Collections_Links'] = From_12421_Until_12999_All_Collections_Links

In [380]:
f = open('From_13000_Until_13545_All_Collections_Links.json')
From_13000_Until_13545_All_Collections_Links = json.load(f)
df_20k_Collections.loc[13000:13544,'Collections_Links'] = From_13000_Until_13545_All_Collections_Links

In [383]:
f = open('From_13546_Until_13999_All_Collections_Links.json')
From_13546_Until_13999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[13546:13998,'Collections_Links'] = From_13546_Until_13999_All_Collections_Links

In [386]:
f = open('From_14000_Until_14170_All_Collections_Links.json')
From_14000_Until_14170_All_Collections_Links = json.load(f)
df_20k_Collections.loc[14000:14169,'Collections_Links'] = From_14000_Until_14170_All_Collections_Links

In [388]:
f = open('From_14171_Until_14603_All_Collections_Links.json')
From_14171_Until_14603_All_Collections_Links = json.load(f)
df_20k_Collections.loc[14171:14602,'Collections_Links'] = From_14171_Until_14603_All_Collections_Links

In [390]:
f = open('From_14604_Until_14999_All_Collections_Links.json')
From_14604_Until_14999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[14604:14998,'Collections_Links'] = From_14604_Until_14999_All_Collections_Links

In [393]:
f = open('From_15000_Until_15625_All_Collections_Links.json')
From_15000_Until_15625_All_Collections_Links = json.load(f)
df_20k_Collections.loc[15000:15624,'Collections_Links'] = From_15000_Until_15625_All_Collections_Links

In [395]:
f = open('From_15626_Until_16499_All_Collections_Links.json')
From_15626_Until_16499_All_Collections_Links = json.load(f)
df_20k_Collections.loc[15626:16498,'Collections_Links'] = From_15626_Until_16499_All_Collections_Links

In [398]:
f = open('From_16500_Until_16860_All_Collections_Links.json')
From_16500_Until_16860_All_Collections_Links = json.load(f)
df_20k_Collections.loc[16500:16859,'Collections_Links'] = From_16500_Until_16860_All_Collections_Links

In [402]:
f = open('From_16861_Until_17499_All_Collections_Links.json')
From_16861_Until_17499_All_Collections_Links = json.load(f)
df_20k_Collections.loc[16861:17498,'Collections_Links'] = From_16861_Until_17499_All_Collections_Links

In [403]:
f = open('From_17500_Until_17720_All_Collections_Links.json')
From_17500_Until_17720_All_Collections_Links = json.load(f)
df_20k_Collections.loc[17500:17719,'Collections_Links'] = From_17500_Until_17720_All_Collections_Links

In [405]:
f = open('From_17721_Until_18082_All_Collections_Links.json')
From_17721_Until_18082_All_Collections_Links = json.load(f)
df_20k_Collections.loc[17721:18081,'Collections_Links'] = From_17721_Until_18082_All_Collections_Links

In [407]:
f = open('From_18083_Until_18346_All_Collections_Links.json')
From_18083_Until_18346_All_Collections_Links = json.load(f)
df_20k_Collections.loc[18083:18345,'Collections_Links'] = From_18083_Until_18346_All_Collections_Links

In [409]:
f = open('From_18347_Until_18466_All_Collections_Links.json')
From_18347_Until_18466_All_Collections_Links = json.load(f)
df_20k_Collections.loc[18347:18465,'Collections_Links'] = From_18347_Until_18466_All_Collections_Links

In [411]:
f = open('From_18467_Until_18499_All_Collections_Links.json')
From_18467_Until_18499_All_Collections_Links = json.load(f)
df_20k_Collections.loc[18467:18498,'Collections_Links'] = From_18467_Until_18499_All_Collections_Links

In [414]:
f = open('From_18500_Until_18613_All_Collections_Links.json')
From_18500_Until_18613_All_Collections_Links = json.load(f)
df_20k_Collections.loc[18500:18612,'Collections_Links'] = From_18500_Until_18613_All_Collections_Links

In [416]:
f = open('From_18614_Until_18869_All_Collections_Links.json')
From_18614_Until_18869_All_Collections_Links = json.load(f)
df_20k_Collections.loc[18614:18868,'Collections_Links'] = From_18614_Until_18869_All_Collections_Links

In [418]:
f = open('From_18870_Until_19412_All_Collections_Links.json')
From_18870_Until_19412_All_Collections_Links = json.load(f)
df_20k_Collections.loc[18870:19411,'Collections_Links'] = From_18870_Until_19412_All_Collections_Links

In [422]:
f = open('From_19413_Until_19749_All_Collections_Links.json')
From_19413_Until_19749_All_Collections_Links = json.load(f)
df_20k_Collections.loc[19413:19748,'Collections_Links'] = From_19413_Until_19749_All_Collections_Links

In [423]:
f = open('From_19750_Until_19999_All_Collections_Links.json')
From_19750_Until_19999_All_Collections_Links = json.load(f)
df_20k_Collections.loc[19750:19998,'Collections_Links'] = From_19750_Until_19999_All_Collections_Links

In [425]:
df_20k_Collections ## finished inserting collections links into dataframe

Collection_Name  Category_Art  \
0                                            A & C             0   
1      A 2D representation of a Brushless DC Motor             0   
2                                A Bathing Kitsune             0   
3                               A Beautiful Nature             0   
4                     A Beautiful moments in Japan             0   
...                                            ...           ...   
19995                                     Over Sky             0   
19996            Over the Fog it feels like Heaven             0   
19997                             Overcast Glacier             0   
19998                     Overheard on Wall Street             0   
19999                                     Overside             0   

       Category_Collectibles  Category_Domain Names  Category_Music  \
0                          0                      0               0   
1                          0                      0               0   
2                          0                      0               0   
3                          0                      0               0   
4                          0                      0               0   
...                      ...                    ...             ...   
19995                      0                      0               0   
19996                      0                      0               0   
19997                      0                      0               0   
19998                      1                      0               0   
19999                      0                      0               0   

       Category_Photography  Category_Sports  Category_Trading Cards  \
0                         0                0                       0   
1                         0                0                       0   
2                         0                0                       1   
3                         1                0                       0   
4                         1                0                       0   
...                     ...              ...                     ...   
19995                     0                0                       0   
19996                     1                0                       0   
19997                     1                0                       0   
19998                     0                0                       0   
19999                     0                0                       0   

       Category_Utility  Category_Virtual Worlds  \
0                     1                        0   
1                     1                        0   
2                     0                        0   
3                     0                        0   
4                     0                        0   
...                 ...                      ...   
19995                 1                        0   
19996                 0                        0   
19997                 0                        0   
19998                 0                        0   
19999                 1                        0   

                                       Collections_Links  
0                                                   None  
1      https://opensea.io/collection/a-2d-representat...  
2          https://opensea.io/collection/abathingkitsune  
3       https://opensea.io/collection/a-beautiful-nature  
4      https://opensea.io/collection/a-beautiful-mome...  
...                                                  ...  
19995             https://opensea.io/collection/over-sky  
19996         https://opensea.io/collection/over-the-fog  
19997     https://opensea.io/collection/overcast-glacier  
19998  https://opensea.io/collection/overheardonwalls...  
19999                                               None  

[20000 rows x 11 columns]

In [429]:
df_20k_Collections_after_excluding_nan = df_20k_Collections.dropna() 
## removing all the rows of collections without links to the collection page

In [434]:
df_20k_Collections_after_excluding_nan.reset_index(drop=True)

Collection_Name  Category_Art  \
0      A 2D representation of a Brushless DC Motor             0   
1                                A Bathing Kitsune             0   
2                               A Beautiful Nature             0   
3                     A Beautiful moments in Japan             0   
4                             A Bird's Perspective             0   
...                                            ...           ...   
18339                                 Over And Out             0   
18340                                     Over Sky             0   
18341            Over the Fog it feels like Heaven             0   
18342                             Overcast Glacier             0   
18343                     Overheard on Wall Street             0   

       Category_Collectibles  Category_Domain Names  Category_Music  \
0                          0                      0               0   
1                          0                      0               0   
2                          0                      0               0   
3                          0                      0               0   
4                          0                      0               0   
...                      ...                    ...             ...   
18339                      1                      0               0   
18340                      0                      0               0   
18341                      0                      0               0   
18342                      0                      0               0   
18343                      1                      0               0   

       Category_Photography  Category_Sports  Category_Trading Cards  \
0                         0                0                       0   
1                         0                0                       1   
2                         1                0                       0   
3                         1                0                       0   
4                         1                0                       0   
...                     ...              ...                     ...   
18339                     0                0                       0   
18340                     0                0                       0   
18341                     1                0                       0   
18342                     1                0                       0   
18343                     0                0                       0   

       Category_Utility  Category_Virtual Worlds  \
0                     1                        0   
1                     0                        0   
2                     0                        0   
3                     0                        0   
4                     0                        0   
...                 ...                      ...   
18339                 0                        0   
18340                 1                        0   
18341                 0                        0   
18342                 0                        0   
18343                 0                        0   

                                       Collections_Links  
0      https://opensea.io/collection/a-2d-representat...  
1          https://opensea.io/collection/abathingkitsune  
2       https://opensea.io/collection/a-beautiful-nature  
3      https://opensea.io/collection/a-beautiful-mome...  
4        https://opensea.io/collection/birds-perspective  
...                                                  ...  
18339       https://opensea.io/collection/over-and-out-1  
18340             https://opensea.io/collection/over-sky  
18341         https://opensea.io/collection/over-the-fog  
18342     https://opensea.io/collection/overcast-glacier  
18343  https://opensea.io/collection/overheardonwalls...  

[18344 rows x 11 columns]

In [435]:
df_20k_Collections_after_excluding_nan.to_csv('df_20k_Collections_after_excluding_nan.csv')
##saving progress of dataframe into csv for later continuation 

In [756]:
def Get_Collections_Features_List(collections_links_list):
    collections_features_lists = []
    lists_counter = 0
    for link in collections_links_list:
        try:
            features_list = Get_collection_features(link)
            if(features_list != False):
                collections_features_lists.append(features_list)
                time.sleep(2)
                lists_counter+=1
                print(lists_counter)
            else:
                break
        except Exception as e:
            print(e)
            print("Error on the",lists_counter+1,"link")
            break
    return collections_features_lists,lists_counter

In [475]:
Collections_Links_list = df_20k_Collections_after_excluding_nan['Collections_Links']

In [778]:
Collections_Links_list_split_first_9000 = Collections_Links_list.loc[0:9000]
Collections_Links_list_split_first_9000_list = Collections_Links_list_split_first_9000.tolist()

In [507]:
Collections_Links_list_split_after_9000 = Collections_Links_list.loc[9000:]
Collections_Links_list_split_after_9000_list = Collections_Links_list_split_after_9000.tolist()

In [508]:
##split the work to 2 group members , each gets 9000 collections to work on to get their features

In [511]:
with open("Collections_Links_list_split_first_9000_list.json", "w") as outfile:
    json.dump(Collections_Links_list_split_first_9000_list, outfile)

In [512]:
with open("Collections_Links_list_split_after_9000_list.json", "w") as outfile:
    json.dump(Collections_Links_list_split_first_9000_list, outfile)

In [684]:
Collections_Features_Lists_First_9000 = Get_Collections_Features_List(Collections_Links_list_split_first_9000_list) 
##building a list of lists that contains the collections features for each collection

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


5139
5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338


6778
6779
6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977


In [711]:
Collections_Features_Lists_First_7245_ = deepcopy(Collections_Features_Lists_First_9000)

In [739]:
Collections_Features_Lists_First_7245_

([['0', '0', None, None],
  [None, None, None, None],
  ['11', '1', ' 0.001', 'https://twitter.com/riteshverma357'],
  ['4', '1', '0.15', None],
  ['4', '1', '0.09', None],
  ['11', '5', '0.011', 'https://twitter.com/TSkoff'],
  ['75', '1', None, None],
  ['0', '0', None, None],
  ['29', '3', '0.1', 'https://twitter.com/TheCutter_5'],
  ['101', '15', '0.015', None],
  ['26', '8', '0.001', 'http://twitter.com/bramk'],
  ['1', '1', None, 'https://www.twitter.com/Prabhavvyas2'],
  ['1', '1', None, None],
  ['750', '264', '0.05', 'https://twitter.com/udinovpro'],
  ['1', '5', '0.002', 'https://www.twitter.com/desrtclub'],
  ['43', '29', '0.35', 'https://www.twitter.com/elusiveilusionz'],
  ['20', '2', '0.05', 'https://www.twitter.com/olboyphotos'],
  ['0', '0', None, None],
  ['8', '1', '0.4', None],
  ['10', '1', None, 'https://twitter.com/BorelliFilip'],
  ['0', '0', None, None],
  ['2', '2', '0.015', 'https://www.twitter.com/tubeblogger'],
  ['2', '1', '1', None],
  ['5', '1', None, Non

In [688]:
with open('Collections_Features_Lists_First_7245_.json', 'w') as f:       # saving progress
    json.dump(Collections_Features_Lists_First_9000,f)

In [770]:
Collections_Links_From_7246_To_9000 = Collections_Links_list_split_first_9000_list[7246:]
Collections_Features_Lists_From_7246_To_9000 = Get_Collections_Features_List(Collections_Links_From_7246_To_9000) 
##building a list of lists that contains the collections features for each collection

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [781]:
Collections_Features_Lists_From_7246_To_8148 = Collections_Features_Lists_From_7246_To_9000

In [784]:
with open('Collections_Features_Lists_From_7246_To_8148.json', 'w') as f:       # saving progress
    json.dump(Collections_Features_Lists_From_7246_To_8148,f)

In [822]:
df =  df_20k_Collections_after_excluding_nan.reset_index(drop=True)

In [823]:
df['Items'] = None
df['Owners'] = None
df['Floor_Price'] = None
df['Twitter_Links'] = None

In [881]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collections_Features_Lists_First_7245_)

In [848]:
new_df = insert_OS_features_into_dataframe(df,0,7244,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)
df.loc[6015,'Floor_Price'] = '60.69' ##data from crypto punks official website

In [210]:
pd.set_option("display.max_rows", None, "display.max_columns", None)

In [133]:
#new_df

In [852]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collections_Features_Lists_From_7246_To_8148)
new_df = insert_OS_features_into_dataframe(new_df,7246,8147,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)

In [887]:
# new_df

In [854]:
new_df.to_csv('df_progress_4.csv') #saving progress

In [855]:
f = open('Collection_feature_8148_until_9094.json')
Collection_feature_8148_until_9094 = json.load(f)

In [858]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_8148_until_9094)
new_df_1 = insert_OS_features_into_dataframe(new_df,8148,9093,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)

In [886]:
# new_df_1

In [865]:
f = open('Collection_feature_9048_until_10414.json')
Collection_feature_9048_until_10414 = json.load(f)

In [872]:
Collection_feature_9094_until_10414 = Collection_feature_9048_until_10414[0][46:]

In [884]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_9094_until_10414)
new_df_2 = insert_OS_features_into_dataframe(new_df_1,9094,10413,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)


In [95]:
#new_df_2

In [890]:
new_df_2.to_csv('df_progress_5_inserting_OS_features.csv') #saving progress

In [127]:
f = open('Collection_feature_10348_until_10911.json')
Collection_feature_10348_until_10911 = json.load(f)

In [128]:
loaded_df = pd.read_csv('df_progress_5_inserting_OS_features.csv')

In [129]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_10348_until_10848[0])
new_df_progress_until_10911 = insert_OS_features_into_dataframe(loaded_df,10348,10911,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)


In [130]:
f = open('Collection_feature_10848_until_11851.json')
Collection_feature_10848_until_11851 = json.load(f)

In [146]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_10848_until_11851[0])
new_df_progress_until_11850 = insert_OS_features_into_dataframe(new_df_progress_until_10911,10848,11850,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)



In [141]:
f = open('Collection_feature_11848_until_13174.json')
Collection_feature_11848_until_13174 = json.load(f)

In [148]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_11848_until_13174[0])
new_df_progress_until_13174 = insert_OS_features_into_dataframe(new_df_progress_until_11850,11848,13173,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)

In [150]:
f = open('Collection_feature_13148_until_14062.json')
Collection_feature_13148_until_14062 = json.load(f)

In [152]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_13148_until_14062[0])
new_df_progress_until_14062 = insert_OS_features_into_dataframe(new_df_progress_until_13174,13148,14061,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)

In [154]:
f = open('Collection_feature_14063_until_15148.json')
Collection_feature_14063_until_15148 = json.load(f)

In [158]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_14063_until_15148[0])
new_df_progress_until_15148 = insert_OS_features_into_dataframe(new_df_progress_until_14062,14063,15147,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)


In [171]:
f = open('Collection_feature_15148_until_16957.json')
Collection_feature_15148_until_16957 = json.load(f)

In [172]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_15148_until_16957[0])
new_df_progress_until_16957 = insert_OS_features_into_dataframe(new_df_progress_until_15148,15148,16956,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)


In [214]:
f = open('Collection_feature_16958_until_17984.json')
Collection_feature_16958_until_17984 = json.load(f)

In [212]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_16958_until_17984[0])
new_df_progress_until_17984 = insert_OS_features_into_dataframe(new_df_progress_until_16957,16958,17983,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)


In [216]:
f = open('Collection_feature_17985_until_the_end.json')
Collection_feature_17985_until_the_end = json.load(f)

In [218]:
Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links = features_lists_extraction(Collection_feature_17985_until_the_end[0])
new_df_progress_until_end = insert_OS_features_into_dataframe(new_df_progress_until_17984,17985,18344,Collections_Items , Collections_Owners , Collections_Floor_Prices , Collections_Twitter_Links)


In [125]:
new_df_progress_until_end_copy = new_df_progress_until_end.copy()

NameError: name 'new_df_progress_until_end' is not defined

In [226]:
new_df_progress_until_end_copy.drop(['Unnamed: 0'], axis = 1 , inplace=True)

In [228]:
new_df_progress_until_end_copy.dropna(inplace=True)

In [230]:
new_df_progress_until_end_copy.reset_index(drop=True)

Collection_Name  Category_Art  \
0                                    A Beautiful Nature             0   
1                                          A Blue World             0   
2                                   A Bridge to Reality             0   
3                                     A Colour Alphabet             1   
4                                            A Cute Cat             0   
5                                     A DESRT HALLOWEEN             0   
6                            A Dance of Light and Water             0   
7                                      A Day With Byron             0   
8                      A Game of Stonks - Mverse Office             0   
9                                   A Glitch in Reality             0   
10                            A Human in Times of Chaos             1   
11                                 A Kalimba Collection             0   
12                              A List Apes V2 Official             0   
13                                       A London Thing             0   
14            A Los Angeles Film Photography Collection             1   
15                           A Martian Storybook Series             1   
16                               A Million Lonely Stars             0   
17                             A Miscellany of Thoughts             1   
18                                     A Moment Forever             0   
19                   A Moment in Time - Sky Photography             0   
20                                  A Mysterious Figure             0   
21                                          A New Light             0   
22    A New Paradigm for Internet Perception, The Cu...             0   
23                                   A New Path Forward             0   
24                                    A New York Moment             0   
25                     A Quarantine Dream by Sam Horine             0   
26                                     A Sense of Scale             0   
27                                       A Silent Movie             0   
28                                      A Slime Appears             0   
29                                     A Spark Of Light             1   
30                        A Step Apart | NFT Short Film             1   
31                                    A Symphony of Fog             0   
32                                      A Trip To Peace             1   
33                           A Unique Unicorn Christmas             0   
34            A Walk on the Beach with Eloise Robbertze             0   
35              A Walk through The Colourless Mountains             0   
36                       A Windy City by The Boca Libre             0   
37                                   A YEAR TO REMEMBER             0   
38                                       A rainbow day.             0   
39                              A sunday in South Italy             0   
40              A tribute to Hua Lamphong in Monochrome             0   
41                                       A wicked Agent             0   
42                                        A//D Film Lab             0   
43                                               AAI 2G             1   
44                                          ABCDJ x GAN             0   
45                                      ABNORMAL ENTITY             1   
46                                             ABRAXXAS             1   
47                                        ABSart ABSart             1   
48                                ABTR - Chinese Zodiac             0   
49                                              ACEOFLA             0   
50                                  ACM CURRENT PLAYERS             0   
51                                          ACM legends             0   
52                                               ACULSW             1   
53                              AD ASTRA - To the Stars             0   
54                       

In [137]:
df_with_OS_features = pd.read_csv('df_with_OS_features_after_cleaning.csv')
df_with_OS_features.drop(['Unnamed: 0'], axis = 1 , inplace=True)
df_with_OS_features.reset_index(drop=True)

Collection_Name  Category_Art  Category_Collectibles  \
0              A Beautiful Nature             0                      0   
1                    A Blue World             0                      0   
2             A Bridge to Reality             0                      0   
3               A Colour Alphabet             1                      0   
4                      A Cute Cat             0                      1   
...                           ...           ...                    ...   
6655  Outlaw Gals Motorcycle Keys             0                      1   
6656                       OvOwls             0                      1   
6657               Ova Libenovo's             0                      0   
6658             Overcast Glacier             0                      0   
6659     Overheard on Wall Street             0                      1   

      Category_Domain Names  Category_Music  Category_Photography  \
0                         0               0                     1   
1                         0               0                     1   
2                         0               0                     1   
3                         0               0                     0   
4                         0               0                     0   
...                     ...             ...                   ...   
6655                      0               0                     0   
6656                      0               0                     0   
6657                      0               1                     0   
6658                      0               0                     1   
6659                      0               0                     0   

      Category_Sports  Category_Trading Cards  Category_Utility  \
0                   0                       0                 0   
1                   0                       0                 0   
2                   0                       0                 0   
3                   0                       0                 0   
4                   0                       0                 0   
...               ...                     ...               ...   
6655                0                       0                 0   
6656                0                       0                 0   
6657                0                       0                 0   
6658                0                       0                 0   
6659                0                       0                 0   

      Category_Virtual Worlds  \
0                           0   
1                           0   
2                           0   
3                           0   
4                           0   
...                       ...   
6655                        0   
6656                        0   
6657                        0   
6658                        0   
6659                        0   

                                      Collections_Links Items  Owners  \
0      https://opensea.io/collection/a-beautiful-nature    11     1.0   
1              https://opensea.io/collection/ablueworld    11     5.0   
2        https://opensea.io/collection/abridgetoreality    29     3.0   
3         https://opensea.io/collection/colour-alphabet    26     8.0   
4                https://opensea.io/collection/acutecat   750   264.0   
...                                                 ...   ...     ...   
6655                 https://opensea.io/collection/ogmk   570   517.0   
6656               https://opensea.io/collection/ovowls    14     5.0   
6657       https://opensea.io/collection/ova-libenovo-s    13     1.0   
6658     https://opensea.io/collection/overcast-glacier     5     1.0   
6659  https://opensea.io/collection/overheardonwalls...     4     3.0   

      Floor_Price                         Twitter_Links  
0           0.001    https://twitter.com/riteshverma357  
1           0.011            https://twitter.com/TSkoff  
2           0.100       https://twitter.com/The

In [464]:
df_with_OS_features.to_csv('df_with_OS_features_after_cleaning_.csv') #saving progress

In [200]:
twitter_links = df_with_OS_features['Twitter_Links']
twitter_usernames = []
for link in twitter_links:
    last_index_before_usernames = link.rfind('/')
    username_ = link[last_index_before_usernames+1:]
    twitter_usernames.append(username_)

In [206]:
api = tweepy_settings()

In [473]:
Twitter_Users_Features = Get_Twitter_Features(twitter_usernames)

403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
4

Rate limit reached. Sleeping for: 402


404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Fou

Rate limit reached. Sleeping for: 550


404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
403 Forbidden
63 - User has been suspended.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not

...

404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not 

Rate limit reached. Sleeping for: 536


404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
403 Forbidden
63 - User has been suspended.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not 

Rate limit reached. Sleeping for: 520


404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.
404 Not Found
50 - User not found.


In [478]:
with open('Twitter_Users_Features_perfect.json', 'w') as f:       # saving progress
    json.dump(Twitter_Users_Features,f)

In [479]:
Twitter_Users_Features

[[10, 327, False, '04/25/2016'],
 [235, 382, False, '12/26/2010'],
 [41, 154, False, '11/30/2021'],
 [24562, 3507, True, '06/06/2009'],
 [2639, 3063, False, '08/25/2011'],
 [5, 42, False, '07/21/2021'],
 [1820, 1266, False, '05/25/2021'],
 [250, 271, False, '01/17/2018'],
 [310, 270, False, '06/25/2013'],
 [32179, 675, False, '09/18/2019'],
 [2536, 380, False, '08/09/2021'],
 [None, None, None, None],
 [397, 179, False, '11/19/2021'],
 [None, None, None, None],
 [2001, 1604, False, '09/12/2021'],
 [1755384, 6226, False, '08/12/2013'],
 [2396, 1000, False, '05/25/2021'],
 [4572, 3768, False, '12/23/2009'],
 [6815, 1164, False, '05/28/2019'],
 [23, 77, False, '08/26/2021'],
 [383, 220, False, '11/03/2021'],
 [1467, 1124, False, '08/05/2009'],
 [517, 792, False, '01/17/2008'],
 [1271, 953, False, '12/02/2020'],
 [978, 342, False, '05/17/2020'],
 [4587, 1217, True, '08/23/2007'],
 [8324, 1299, False, '09/22/2010'],
 [21971, 5724, False, '12/22/2009'],
 [8, 53, False, '06/15/2021'],
 [33682

In [484]:
users_followers_count = []
users_following_count = []
users_is_verified_count = []
users_creation_date_count = []
for user in Twitter_Users_Features:
    users_followers_count.append(user[0])
    users_following_count.append(user[1])
    users_is_verified_count.append(user[2])
    users_creation_date_count.append(user[3])

In [489]:
df_with_OS_features['Twitter_Page_Followers'] = users_followers_count
df_with_OS_features['Twitter_Page_Following'] = users_following_count
df_with_OS_features['Twitter_Page_Is_Verified'] = users_is_verified_count
df_with_OS_features['Twitter_Page_Creation_Date'] = users_creation_date_count

In [491]:
df_with_OS_features_copy = df_with_OS_features.copy()

In [499]:
df_with_OS_features_copy.dropna(inplace=True)
df_exclude_volume = df_with_OS_features_copy.reset_index(drop=True)

In [36]:
df_exclude_volume = pd.read_csv('df_exclude_volume_and_engagements.csv')

In [21]:
twitter_links = df_exclude_volume['Twitter_Links']
twitter_usernames = []
for link in twitter_links:
    last_index_before_usernames = link.rfind('/')
    username_ = link[last_index_before_usernames+1:]
    twitter_usernames.append(username_)

In [22]:
users_enagements_list_from_3128_until_end = Get_Twitter_user_engagement(twitter_usernames[3128:])

user 0
user 1
user 2
user 3
user 4
user 5
user 6
user 7
user 8
user 9
user 10
user 11
user 12
user 13
user 14
user 15
user 16
user 17
user 18
user 19
user 20
user 21
user 22
user 23
user 24
user 25
user 26
user 27
user 28
user 29
user 30
user 31
user 32
401 Unauthorized
user 33
user 34
user 35
user 36
user 37
user 38
user 39
user 40
user 41
user 42
user 43
user 44
user 45
user 46
user 47
user 48
user 49
user 50
user 51
user 52
user 53
user 54
user 55
user 56
user 57
user 58
user 59
user 60
user 61
user 62
user 63
user 64
user 65
user 66
user 67
user 68
user 69
user 70
user 71
user 72
user 73
user 74
user 75
user 76
user 77
user 78
user 79
user 80
user 81
user 82
user 83
user 84
user 85
user 86
user 87
user 88
user 89
user 90
user 91
user 92
user 93
user 94
user 95
user 96
user 97
user 98
user 99
user 100
user 101
user 102
user 103
user 104
user 105
user 106
user 107
user 108
user 109
user 110
user 111
user 112
user 113
user 114
user 115
user 116
user 117


Rate limit reached. Sleeping for: 426


user 118
user 119
user 120
user 121
user 122
user 123
user 124
user 125
user 126
user 127
user 128
user 129
user 130
user 131
user 132
user 133
user 134
user 135
user 136
user 137
user 138
user 139
user 140
user 141
user 142
user 143
user 144
user 145
user 146
user 147
user 148
user 149
user 150
user 151
user 152
user 153
user 154
user 155
user 156
user 157
user 158
user 159
user 160
user 161
user 162
user 163
user 164
user 165
user 166
user 167
user 168
user 169
user 170
user 171
user 172
user 173
user 174
user 175
user 176
user 177
user 178
user 179
user 180
user 181
user 182
user 183
user 184
user 185
user 186
user 187
user 188
user 189
user 190
user 191
user 192
user 193
user 194
user 195
user 196
user 197
user 198
user 199
user 200
user 201
user 202
user 203
user 204
user 205
user 206
user 207
user 208
user 209
user 210
user 211
user 212
user 213
user 214
user 215
user 216
user 217
user 218
user 219
user 220
user 221
user 222
user 223
user 224
user 225
user 226
user 227
user 228
u

Rate limit reached. Sleeping for: 419


user 246
user 247
user 248
user 249
user 250
user 251
401 Unauthorized
user 252
user 253
user 254
user 255
user 256
user 257
user 258
user 259
user 260
user 261
user 262
user 263
user 264
user 265
user 266
user 267
user 268
user 269
user 270
user 271
user 272
user 273
user 274
user 275
user 276
user 277
user 278
user 279
user 280
user 281
user 282
user 283
user 284
user 285
user 286
user 287
user 288
user 289
user 290
user 291
user 292
user 293
user 294
user 295
user 296
user 297
user 298
user 299
user 300
user 301
user 302
user 303
user 304
user 305
user 306
user 307
user 308
user 309
user 310
user 311
user 312
user 313
user 314
user 315
user 316
user 317
user 318
user 319
user 320
user 321
user 322
user 323
user 324
user 325
user 326
user 327
user 328
user 329
user 330
user 331
user 332
user 333
user 334
user 335
user 336
user 337
user 338
user 339
user 340
user 341
user 342
user 343
user 344
user 345
user 346
user 347
user 348
user 349
user 350
user 351
user 352
user 353
user 354
us

...

user 2769
user 2770
user 2771
user 2772
user 2773
user 2774
user 2775
user 2776
user 2777
user 2778
user 2779
user 2780
user 2781
user 2782
user 2783
user 2784
user 2785
user 2786
user 2787
user 2788
user 2789
user 2790
user 2791
user 2792
user 2793
user 2794
user 2795
user 2796
user 2797
user 2798
user 2799
user 2800
user 2801
user 2802
user 2803
user 2804
user 2805
user 2806
user 2807
user 2808
user 2809
user 2810
user 2811
user 2812
user 2813
user 2814
user 2815
user 2816
user 2817
user 2818
user 2819
user 2820
user 2821
user 2822
user 2823
user 2824
user 2825
user 2826
user 2827
user 2828
user 2829
user 2830
user 2831
user 2832
user 2833
user 2834
user 2835
user 2836
user 2837
user 2838
user 2839
user 2840
user 2841
user 2842
user 2843
user 2844
user 2845
user 2846
user 2847
user 2848
user 2849
user 2850
user 2851
user 2852
user 2853
user 2854
user 2855
user 2856
user 2857
user 2858
user 2859
user 2860
user 2861
user 2862
user 2863
user 2864
user 2865
user 2866
user 2867
user 2868


Rate limit reached. Sleeping for: 452


user 2895
user 2896
user 2897
user 2898
user 2899
user 2900
404 Not Found
34 - Sorry, that page does not exist.
user 2901
user 2902
user 2903
user 2904
user 2905
user 2906
user 2907
user 2908
user 2909
user 2910
user 2911
400 Bad Request
The number of values in the `ids` query parameter list [0] is not between 1 and 100
user 2912
user 2913
user 2914
user 2915
user 2916
user 2917
user 2918
user 2919
user 2920
user 2921
user 2922
user 2923
user 2924
user 2925
user 2926
user 2927
user 2928
user 2929
user 2930
user 2931
user 2932
user 2933
user 2934
user 2935
user 2936
user 2937
user 2938
user 2939
user 2940
user 2941
user 2942
user 2943
user 2944
user 2945
user 2946
user 2947
user 2948
user 2949
user 2950
user 2951
user 2952
user 2953
user 2954
user 2955
user 2956
user 2957
user 2958
user 2959
user 2960
user 2961
user 2962
user 2963
user 2964
user 2965
user 2966
user 2967
400 Bad Request
The number of values in the `ids` query parameter list [0] is not between 1 and 100
user 2968
user 296

Rate limit reached. Sleeping for: 453


user 3010
user 3011
user 3012
user 3013
user 3014
user 3015
user 3016
user 3017
user 3018
user 3019
user 3020
user 3021
user 3022
user 3023
user 3024
user 3025
user 3026
user 3027
user 3028
user 3029
user 3030
user 3031
user 3032
user 3033
user 3034
user 3035
user 3036
user 3037
user 3038
user 3039
user 3040
user 3041
user 3042
user 3043
user 3044
user 3045
user 3046
user 3047
user 3048
user 3049
user 3050
user 3051
user 3052
user 3053
user 3054
user 3055
user 3056
user 3057
user 3058
user 3059
user 3060
user 3061
user 3062
user 3063
user 3064
user 3065
user 3066
user 3067
user 3068
user 3069
user 3070
user 3071
user 3072
user 3073
user 3074
user 3075
user 3076
user 3077
user 3078
user 3079
400 Bad Request
The number of values in the `ids` query parameter list [0] is not between 1 and 100
user 3080
user 3081
user 3082
user 3083
user 3084
user 3085
user 3086
user 3087
user 3088
user 3089
user 3090
user 3091
400 Bad Request
The number of values in the `ids` query parameter list [0] is no

In [24]:
with open('users_enagements_list_from_3128_until_end.json', 'w') as f:       # saving progress
    json.dump(users_enagements_list_from_3128_until_end,f)

In [35]:
max_retweets_count_until_3127 = []
max_replis_count_until_3127 = []
max_likes_count_until_3127 = []
max_quotes_count_until_3127 = []

f = open('users_enagements_list_until_3127.json')
users_enagements_list_until_3127 = json.load(f)
for feature in users_enagements_list_until_3127:
    max_retweets_count_until_3127.append(feature[0])
    max_replis_count_until_3127.append(feature[1])
    max_likes_count_until_3127.append(feature[2])
    max_quotes_count_until_3127.append(feature[3])   

In [47]:
df_exclude_volume['Max_Twitter_Retweets'] = None
df_exclude_volume['Max_Twitter_Replies'] = None
df_exclude_volume['Max_Twitter_Likes'] = None
df_exclude_volume['Max_Twitter_Quotes'] = None
df_exclude_volume.loc[:3126,'Max_Twitter_Retweets'] = max_retweets_count_until_3127
df_exclude_volume.loc[:3126,'Max_Twitter_Replies'] = max_replis_count_until_3127
df_exclude_volume.loc[:3126,'Max_Twitter_Likes'] = max_likes_count_until_3127
df_exclude_volume.loc[:3126,'Max_Twitter_Quotes'] = max_quotes_count_until_3127

In [49]:
max_retweets_count_from_3128_until_end = []
max_replis_count_from_3128_until_end = []
max_likes_count_from_3128_until_end = []
max_quotes_count_from_3128_until_end = []

for feature in users_enagements_list_from_3128_until_end:
    max_retweets_count_from_3128_until_end.append(feature[0])
    max_replis_count_from_3128_until_end.append(feature[1])
    max_likes_count_from_3128_until_end.append(feature[2])
    max_quotes_count_from_3128_until_end.append(feature[3])   
df_exclude_volume.loc[3128:,'Max_Twitter_Retweets'] = max_retweets_count_from_3128_until_end
df_exclude_volume.loc[3128:,'Max_Twitter_Replies'] = max_replis_count_from_3128_until_end
df_exclude_volume.loc[3128:,'Max_Twitter_Likes'] = max_likes_count_from_3128_until_end
df_exclude_volume.loc[3128:,'Max_Twitter_Quotes'] = max_quotes_count_from_3128_until_end    

In [54]:
df_exclude_volume_copy = df_exclude_volume.copy()

In [57]:
df_exclude_volume_copy.dropna(inplace=True)

In [59]:
df_exclude_volume_copy.reset_index(drop=True)

Collection_Name  Category_Art  Category_Collectibles  \
0              A Beautiful Nature             0                      0   
1                    A Blue World             0                      0   
2             A Bridge to Reality             0                      0   
3               A Colour Alphabet             1                      0   
4                      A Cute Cat             0                      1   
...                           ...           ...                    ...   
6156  Outlaw Gals Motorcycle Keys             0                      1   
6157                       OvOwls             0                      1   
6158               Ova Libenovo's             0                      0   
6159             Overcast Glacier             0                      0   
6160     Overheard on Wall Street             0                      1   

      Category_Domain Names  Category_Music  Category_Photography  \
0                         0               0                     1   
1                         0               0                     1   
2                         0               0                     1   
3                         0               0                     0   
4                         0               0                     0   
...                     ...             ...                   ...   
6156                      0               0                     0   
6157                      0               0                     0   
6158                      0               1                     0   
6159                      0               0                     1   
6160                      0               0                     0   

      Category_Sports  Category_Trading Cards  Category_Utility  \
0                   0                       0                 0   
1                   0                       0                 0   
2                   0                       0                 0   
3                   0                       0                 0   
4                   0                       0                 0   
...               ...                     ...               ...   
6156                0                       0                 0   
6157                0                       0                 0   
6158                0                       0                 0   
6159                0                       0                 0   
6160                0                       0                 0   

      Category_Virtual Worlds  ... Floor_Price  \
0                           0  ...       0.001   
1                           0  ...       0.011   
2                           0  ...       0.100   
3                           0  ...       0.001   
4                           0  ...       0.050   
...                       ...  ...         ...   
6156                        0  ...       0.014   
6157                        0  ...       0.010   
6158                        0  ...       0.010   
6159                        0  ...       0.007   
6160                        0  ...      15.439   

                             Twitter_Links  Twitter_Page_Followers  \
0       https://twitter.com/riteshverma357                    10.0   
1               https://twitter.com/TSkoff                   235.0   
2          https://twitter.com/TheCutter_5                    41.0   
3                 http://twitter.com/bramk                 24562.0   
4            https://twitter.com/udinovpro                  2639.0   
...                                    ...                     ...   
6156  https://www.twitter.com/OutlawGalsMC                  3020.0   
6157    https://twitter.com/OvOwlsOfficial                     9.0   
6158   https://www.twitter.com/ovalibenovo                   729.0   
6159        https://twitter.com/BinKlumbDC                   576.0   
6160  https://www.twitter.com/ohwallstreet                  2187.0   

      Twitter_Page_Following Twitter_Page_Is_Verified

In [178]:
df_exclude_OS_new_features = pd.read_csv('df_exclude_OS_new_features.csv')

In [143]:
collections_links = df_exclude_OS_new_features['Collections_Links']
collections_slugs = []
for link in collections_links:
    last_index_before_slug = link.rfind('/')
    slug = link[last_index_before_slug+1:]
    collections_slugs.append(slug)

In [150]:
opensea_collections_features_list = Get_Opensea_Features(collections_slugs)

collection 0
collection 1
collection 2
collection 3
collection 4
collection 5
collection 6
collection 7
collection 8
collection 9
collection 10
collection 11
collection 12
collection 13
collection 14
collection 15
collection 16
collection 17
collection 18
collection 19
collection 20
collection 21
collection 22
collection 23
collection 24
collection 25
collection 26
collection 27
collection 28
collection 29
collection 30
collection 31
collection 32
collection 33
collection 34
collection 35
collection 36
collection 37
collection 38
collection 39
collection 40
collection 41
collection 42
collection 43
collection 44
collection 45
collection 46
collection 47
collection 48
collection 49
collection 50
collection 51
collection 52
collection 53
collection 54
collection 55
collection 56
collection 57
collection 58
collection 59
collection 60
collection 61
collection 62
collection 63
collection 64
collection 65
collection 66
collection 67
collection 68
collection 69
collection 70
collection 71
co

collection 549
collection 550
collection 551
collection 552
collection 553
collection 554
collection 555
collection 556
collection 557
collection 558
collection 559
collection 560
collection 561
collection 562
collection 563
collection 564
collection 565
collection 566
collection 567
collection 568
collection 569
collection 570
collection 571
collection 572
collection 573
collection 574
collection 575
collection 576
collection 577
collection 578
collection 579
collection 580
collection 581
collection 582
collection 583
collection 584
collection 585
collection 586
collection 587
collection 588
collection 589
collection 590
collection 591
collection 592
collection 593
collection 594
collection 595
collection 596
collection 597
collection 598
collection 599
collection 600
collection 601
collection 602
collection 603
collection 604
collection 605
collection 606
collection 607
collection 608
collection 609
collection 610
collection 611
collection 612
collection 613
collection 614
collection

collection 1087
collection 1088
collection 1089
collection 1090
collection 1091
collection 1092
collection 1093
collection 1094
collection 1095
collection 1096
collection 1097
collection 1098
collection 1099
collection 1100
collection 1101
collection 1102
collection 1103
collection 1104
collection 1105
collection 1106
collection 1107
collection 1108
collection 1109
collection 1110
collection 1111
collection 1112
collection 1113
collection 1114
collection 1115
collection 1116
collection 1117
collection 1118
collection 1119
[Errno Expecting value] : 0
collection 1120
collection 1121
collection 1122
collection 1123
collection 1124
collection 1125
collection 1126
collection 1127
collection 1128
collection 1129
collection 1130
collection 1131
collection 1132
collection 1133
collection 1134
collection 1135
collection 1136
collection 1137
collection 1138
collection 1139
collection 1140
collection 1141
collection 1142
collection 1143
collection 1144
collection 1145
collection 1146
collection 1

collection 1597
collection 1598
collection 1599
collection 1600
collection 1601
collection 1602
collection 1603
collection 1604
collection 1605
collection 1606
collection 1607
collection 1608
collection 1609
collection 1610
collection 1611
collection 1612
collection 1613
collection 1614
collection 1615
collection 1616
collection 1617
collection 1618
collection 1619
collection 1620
collection 1621
collection 1622
collection 1623
collection 1624
collection 1625
collection 1626
collection 1627
collection 1628
collection 1629
collection 1630
collection 1631
collection 1632
collection 1633
collection 1634
collection 1635
collection 1636
collection 1637
collection 1638
collection 1639
collection 1640
collection 1641
collection 1642
collection 1643
collection 1644
collection 1645
collection 1646
collection 1647
collection 1648
collection 1649
collection 1650
collection 1651
collection 1652
collection 1653
collection 1654
collection 1655
collection 1656
collection 1657
collection 1658
collecti

collection 2110
collection 2111
collection 2112
collection 2113
collection 2114
collection 2115
collection 2116
collection 2117
collection 2118
collection 2119
collection 2120
collection 2121
collection 2122
collection 2123
collection 2124
collection 2125
collection 2126
collection 2127
collection 2128
collection 2129
collection 2130
collection 2131
collection 2132
collection 2133
collection 2134
collection 2135
collection 2136
collection 2137
collection 2138
collection 2139
collection 2140
collection 2141
collection 2142
collection 2143
collection 2144
collection 2145
collection 2146
collection 2147
collection 2148
collection 2149
collection 2150
collection 2151
collection 2152
collection 2153
collection 2154
collection 2155
collection 2156
collection 2157
collection 2158
collection 2159
collection 2160
collection 2161
collection 2162
collection 2163
collection 2164
collection 2165
collection 2166
collection 2167
collection 2168
collection 2169
collection 2170
collection 2171
collecti

...

collection 4152
collection 4153
collection 4154
collection 4155
collection 4156
collection 4157
collection 4158
collection 4159
collection 4160
collection 4161
collection 4162
collection 4163
collection 4164
collection 4165
collection 4166
collection 4167
collection 4168
collection 4169
collection 4170
collection 4171
collection 4172
collection 4173
collection 4174
collection 4175
collection 4176
collection 4177
collection 4178
collection 4179
collection 4180
collection 4181
collection 4182
collection 4183
collection 4184
collection 4185
collection 4186
collection 4187
collection 4188
collection 4189
collection 4190
collection 4191
collection 4192
collection 4193
collection 4194
collection 4195
collection 4196
collection 4197
collection 4198
collection 4199
collection 4200
collection 4201
collection 4202
collection 4203
collection 4204
collection 4205
collection 4206
collection 4207
collection 4208
collection 4209
collection 4210
collection 4211
collection 4212
collection 4213
collecti

collection 4661
collection 4662
collection 4663
collection 4664
collection 4665
collection 4666
collection 4667
collection 4668
collection 4669
collection 4670
collection 4671
collection 4672
collection 4673
collection 4674
collection 4675
collection 4676
collection 4677
collection 4678
collection 4679
collection 4680
collection 4681
collection 4682
collection 4683
collection 4684
collection 4685
collection 4686
collection 4687
collection 4688
collection 4689
collection 4690
collection 4691
collection 4692
collection 4693
collection 4694
collection 4695
collection 4696
collection 4697
collection 4698
collection 4699
collection 4700
collection 4701
collection 4702
collection 4703
collection 4704
collection 4705
collection 4706
collection 4707
collection 4708
collection 4709
collection 4710
collection 4711
collection 4712
collection 4713
collection 4714
collection 4715
collection 4716
collection 4717
collection 4718
collection 4719
collection 4720
collection 4721
collection 4722
collecti

collection 5138
collection 5139
collection 5140
collection 5141
collection 5142
collection 5143
collection 5144
collection 5145
collection 5146
collection 5147
collection 5148
collection 5149
collection 5150
collection 5151
collection 5152
collection 5153
collection 5154
collection 5155
collection 5156
collection 5157
collection 5158
collection 5159
collection 5160
collection 5161
collection 5162
collection 5163
collection 5164
collection 5165
collection 5166
collection 5167
collection 5168
collection 5169
collection 5170
collection 5171
collection 5172
collection 5173
collection 5174
collection 5175
collection 5176
collection 5177
collection 5178
collection 5179
collection 5180
collection 5181
collection 5182
collection 5183
collection 5184
collection 5185
collection 5186
collection 5187
collection 5188
collection 5189
collection 5190
collection 5191
collection 5192
collection 5193
collection 5194
collection 5195
collection 5196
collection 5197
collection 5198
collection 5199
collecti

collection 5649
collection 5650
collection 5651
collection 5652
collection 5653
collection 5654
collection 5655
collection 5656
collection 5657
collection 5658
collection 5659
collection 5660
collection 5661
collection 5662
collection 5663
collection 5664
collection 5665
collection 5666
'collection'
collection 5667
collection 5668
collection 5669
collection 5670
collection 5671
collection 5672
collection 5673
collection 5674
collection 5675
collection 5676
collection 5677
collection 5678
collection 5679
collection 5680
collection 5681
collection 5682
collection 5683
collection 5684
collection 5685
collection 5686
collection 5687
collection 5688
collection 5689
collection 5690
collection 5691
collection 5692
collection 5693
collection 5694
collection 5695
collection 5696
collection 5697
collection 5698
collection 5699
collection 5700
collection 5701
collection 5702
collection 5703
collection 5704
collection 5705
collection 5706
collection 5707
collection 5708
collection 5709
collection 

collection 6160


In [174]:
with open('opensea_collections_features_list.json', 'w') as f:       # saving progress
    json.dump(opensea_collections_features_list,f)

In [175]:
collections_date = []
collections_30_day_volume = []
collections_safelist_status = []
collections_traits_count = []
for feature in opensea_collections_features_list:
    collections_date.append(feature[0])
    collections_30_day_volume.append(feature[1])
    collections_safelist_status.append(feature[2])
    collections_traits_count.append(feature[3])
    
     

In [179]:
df_exclude_OS_new_features['Collection_Creation_Date'] = collections_date
df_exclude_OS_new_features['Collection_30_Day_Volume'] = collections_30_day_volume
df_exclude_OS_new_features['Collection_Listing_Status'] = collections_safelist_status
df_exclude_OS_new_features['Collection_Traits_count'] = collections_traits_count

In [182]:
df_exclude_OS_new_features_copy = df_exclude_OS_new_features.copy()

In [183]:
df_exclude_OS_new_features_copy.dropna(inplace=True)

In [184]:
df_exclude_OS_new_features_copy.reset_index(drop=True)

Unnamed: 0              Collection_Name  Category_Art  \
0              1                 A Blue World             0   
1              3            A Colour Alphabet             1   
2              4                   A Cute Cat             0   
3              5            A DESRT HALLOWEEN             0   
4              6   A Dance of Light and Water             0   
...          ...                          ...           ...   
5454        6241                 Outdoor Days             0   
5455        6242               Outlaw Gals MC             0   
5456        6243  Outlaw Gals Motorcycle Keys             0   
5457        6245               Ova Libenovo's             0   
5458        6247     Overheard on Wall Street             0   

      Category_Collectibles  Category_Domain Names  Category_Music  \
0                         0                      0               0   
1                         0                      0               0   
2                         1                      0               0   
3                         0                      0               0   
4                         0                      0               0   
...                     ...                    ...             ...   
5454                      0                      0               0   
5455                      1                      0               0   
5456                      1                      0               0   
5457                      0                      0               1   
5458                      1                      0               0   

      Category_Photography  Category_Sports  Category_Trading Cards  \
0                        1                0                       0   
1                        0                0                       0   
2                        0                0                       0   
3                        0                0                       1   
4                        1                0                       0   
...                    ...              ...                     ...   
5454                     1                0                       0   
5455                     0                0                       0   
5456                     0                0                       0   
5457                     0                0                       0   
5458                     0                0                       0   

      Category_Utility  ...  Twitter_Page_Is_Verified  \
0                    0  ...                     False   
1                    0  ...                      True   
2                    0  ...                     False   
3                    0  ...                     False   
4                    0  ...                     False   
...                ...  ...                       ...   
5454                 0  ...                     False   
5455                 0  ...                     False   
5456                 0  ...                     False   
5457                 0  ...                     False   
5458                 0  ...                     False   

     Twitter_Page_Creation_Date Max_Twitter_Retweets  Max_Twitter_Replies  \
0                    12/26/2010                    3                    1   
1                    06/06/2009                   15                    7   
2                    08/25/2011                    4                    3   
3                    07/21/2021                    1                    1   
4                    05/25/2021                    2                    2   
...                         ...                  ...                  ...   
5454                 04/25/2021                    7                    2   
5455                 08/18/2021                  112                  101   
5456                 08/18/2021                  112                  101   
5457                 05/27/2011                   21                    4   
5458                 11

In [200]:
Final_DataFrame_Before_Cleaning = pd.read_csv('Final_DataFrame_Before_Cleaning.csv')

In [202]:
Final_DataFrame_Before_Cleaning.drop(['Unnamed: 0'], axis = 1 , inplace=True)

In [203]:
Final_DataFrame_Before_Cleaning.drop(['Unnamed: 0.1'], axis = 1 , inplace=True)

In [204]:
Final_DataFrame_Before_Cleaning.drop(['Collections_Links'], axis = 1 , inplace=True)

In [205]:
Final_DataFrame_Before_Cleaning.drop(['Twitter_Links'], axis = 1 , inplace=True)

In [207]:
Final_DataFrame_Before_Cleaning.to_csv('Final_DataFrame_Before_Cleaning_1.csv')

In [215]:
Final_DataFrame_Before_Cleaning_copy = Final_DataFrame_Before_Cleaning.copy()

In [216]:
Final_DataFrame_Before_Cleaning_copy['Collection_30_Day_Volume'].replace(to_replace=0.000000,value='None',inplace=True)


In [223]:
Final_DataFrame_Before_Cleaning_copy = Final_DataFrame_Before_Cleaning_copy.replace(to_replace='None', value=np.nan).dropna()

In [225]:
Final_DataFrame_Before_Cleaning_copy = Final_DataFrame_Before_Cleaning_copy.reset_index(drop=True)

In [227]:
Final_DataFrame_After_Scrape = Final_DataFrame_Before_Cleaning_copy

In [228]:
Final_DataFrame_After_Scrape.to_csv('Final_DataFrame_After_Scrape.csv')